# Topic analysis based on Genius songs lyrics

Author : lievre.thomas@gmail.com

---

In this notebook, we will explore the genius data extract from [Kaggle](https://www.kaggle.com/datasets/carlosgdcj/genius-song-lyrics-with-language-information).

**The aim of this analysis is to retrieve topic from lyrics and retrieve main topics by year or decade.**

This notebook was carried out in the context of a class project imposed by the [text mining course (TDDE16)](https://www.ida.liu.se/~TDDE16/project.en.shtml) of Linköpings universitet.


## Few informations about Genius website

Genius is an American digital company founded on August 27, 2009, by Tom Lehman, lan Zechory, and Mahbod Moghadam. Originally launched as Rap Genius with a focus on hip-hop music, it was initially a crowdsourced website where people could fill in the lyrics of rap music and give an interpretation of the lyrics. Over the years the site has grown to contain several million annotated texts from all eras ( from [Wikipedia Genius page](https://en.wikipedia.org/wiki/Genius_(company))).


## Load the data in memory

Data are all contain in a big 9GB csv file (around 5 millions rows). It could be difficult to load all this data in our computer memory. To deal with this issue, I made a loading class to split the data in 6 pickles files to improve the compressness of the data which aim to improve the loading speed in the memory. Then the pickles are randomly draw to improve generality of the data. We currently assumed the data pickles batch are identically distributed (we will explore the data batches at the second part). The class below deal with all the process.

In [1]:
import pandas as pd
from random import seed, sample
import pickle
import glob
import os

class Loader():

    def __init__(self, in_path, out_path):
        """
        Args:
            in_path (str): csv input path.
            out_path (str): Output directory path to store the pickles.
            chunksize (int, optional): Chunksize for DataFrame reader. Defaults to 10**6. 
        """

        self.__in_path = in_path
        self.__out_path = out_path
        self.__chunksize = 10**6

    def __produce_pickles(self):
        """produce pickles by reading csv by chunksize
        """
        with pd.read_csv(self.__in_path, chunksize = self.__chunksize) as reader:
            try:
                os.makedirs(self.__out_path)
            except FileExistsError:
                # directory already exists
                pass
            for i, chunk in enumerate(reader):
                out_file = self.__out_path + "/data_{}.pkl".format(i+1)
                with open(out_file, "wb") as f:
                    pickle.dump(chunk, f, pickle.HIGHEST_PROTOCOL)
    
    def load_pickle(self, pickle_id):
        """load a pickle file by id

        Args:
            pickle_id (int): pickle id.

        Raises:
            Exception: The path of the given id isn't a file

        Returns:
            obj: DataFrame
        """
        # produce the pickles if the directory not exists or
        # if the directory is empty 
        if (not os.path.exists(self.__out_path)) or \
              (len(os.listdir(self.__out_path)) == 0):
            self.__produce_pickles()
        
        # get the file path following the pickle_id
        # given in parameter
        file_path = self.__out_path + \
            "/data_" + str(pickle_id) + ".pkl"

        if os.path.isfile(file_path):
            df = pd.read_pickle(file_path)
        else:
            raise Exception("The pickle file data_{}.pkl doesn't exist".format(pickle_id))
        return df
        

    def random_pickles(self, n_pickles = 3, init = 42, verbose = True):
        """random reader over pickles files

        Args:
            n_pickles (int, optional): number of pickles to load. Defaults to 3.
            init (int, optional): Integer given to the random seed. Defaults to 42.
            verbose (bool, optional): Print the loaded files. Defaults to True

        Raises:
            Exception: Stop the process if n_pickles exceed pickle files number.

        Returns:
            obj: pd.Dataframe
        """

        # produce the pickles if the directory not exists or
        # if the directory is empty 
        if (not os.path.exists(self.__out_path)) or \
              (len(os.listdir(self.__out_path)) == 0):
            self.__produce_pickles()

        pickle_files = [name for name in
                        glob.glob(self.__out_path + "/data_*.pkl")]
        # draw p_files        
        seed(init)

        if n_pickles <= 6:
            random_p_files = sample(pickle_files, n_pickles)
        else:
            raise Exception("The parameter n_pickles (" +
                            "{}) exceed the numbers of pickle files ({})"\
                                .format(n_pickles, len(pickle_files)))
        # print the drawed files
        if verbose:
            print("Loaded pickles:")
            for p in random_p_files:
                print(p)

        # load random pickles file
        df_list = [pd.read_pickle(p) for p in random_p_files]

        # create the dataframe by concatenate the previous
        # dataframes list
        df = pd.concat(df_list, ignore_index = True)
        return df

In [2]:
# create reader
#  /!\ change path in kaggle
kaggle_input = "/kaggle/input/genius-song-lyrics-with-language-information/song_lyrics.csv"
kaggle_output = "/kaggle/working/data/"

# initiate the file loader
loader = Loader(in_path = kaggle_input, out_path = kaggle_output)

# load random pickle files
df = loader.random_pickles(n_pickles = 1)

Loaded pickles:
/kaggle/working/data/data_3.pkl


Batchs of data are randomly loaded in the memory. The number of batchs loaded depends on the memory capacity of the computer running the script. For the analysis, we will only works on the random samples loaded (All the data in Kaggle).  

## Exploring the coarse data

Let's visualize and explore the coarse data before a part of deeper analysis.

In [3]:
df.head()

title   tag        artist  year  views               features  \
0           Roses  rock         Vitja  2017    399                     {}   
1  Keep On Pushin   rap       Problem  2017    692  {"My Princess Aeryn"}   
2          Inside   pop  The jepettos  2017   1302                     {}   
3  Girls Like You    rb      PnB Rock  2017  60114                     {}   
4        Froideur   rap   N'Dirty Deh  2017   5813      {"N\\'Dirty Deh"}   

                                              lyrics       id language_cld3  \
0  The roses start to wither\nWhere the devil lay...  3019113            en   
1  [Hook]\nImma keep on pushin\nImma keep on push...  3019114            en   
2  [Intro]\nOoh, ooh, ah, ah (x2)\n\n[Verse 1]\nI...  3019115            en   
3  [Chorus]\nBaby it was real\nYeah we were the b...  3019117            en   
4  [Refrain]\nEt j'ai perdu la foi, mais c'est pa...  3019120            fr   

  language_ft language  
0          en       en  
1          en       en  
2          en       en  
3          en       en  
4          fr       fr

For each songs, we've got several informations :
- title of the song
- the tag (which kind of music)
- the artist singer name
- the release year
- the number of page views
- the featuring artists names
- the lyrics
- the genius identifier
- Lyrics language according to [CLD3](https://github.com/google/cld3). Not reliable results are NaN. CLD3 is a neural network model for language indentification.
- Lyrics language according to [FastText's langid](https://fasttext.cc/docs/en/language-identification.html). Values with low confidence (<0.5) are NaN. FastText's langid is library developped by Facebook’s AI Research lab for efficient learning of word representations and sentence classification. fastText has also published a fast and accurate tool for text-based language identification capable of recognizing more than 170 languages.
- Combines language_cld3 and language_ft. Only has a non NaN entry if they both "agree".

More information at this link : https://www.kaggle.com/datasets/carlosgdcj/genius-song-lyrics-with-language-information

In [4]:
df.dtypes

title            object
tag              object
artist           object
year              int64
views             int64
features         object
lyrics           object
id                int64
language_cld3    object
language_ft      object
language         object
dtype: object

In [5]:
# display the size
print('Data frame size (row x columns):', df.size)
print('Data rows number: ', len(df))
print('Number of unique songs (following genius id): ', len(df.id.unique()))

Data frame size (row x columns): 11000000
Data rows number:  1000000
Number of unique songs (following genius id):  1000000


Genius id seems to be the unique rows identifier.

Let's vizualise size of the coarse data over years before preprocessing to compare batch distributions. One things to know before vizualise the data, the pickles are create by chunks reading. 

The last diplayed table gives us some information about the data. The csv file seems to be sort by id, so the pickle files are then sort too.

In [6]:
import plotly.express as px
import plotly.io as pio

# change theme template for every graph below
pio.templates.default = "plotly_white"


# get some information about the pickle data
def pickle_informations(data = loader):
    rows = []
    for i in range(1, len(os.listdir('data')) + 1):
        df = data.load_pickle(i)
        rows.append(len(df))
        del df
    return rows

# get the rows
rows = pickle_informations()

# create the dataframe
df_data = pd.DataFrame(
    {'batch' : ['data ' + str(i) for i in range(1,len(rows) + 1)],
    'rows' : rows})

fig = px.bar(df_data, x="batch", y="rows")
fig.show()

Batch seems to have the same number of rows rexcept for the last one which is consistent because batch are create iteratively by 10e6 chunks over the csv The last batch could be seen as a rest.

In [7]:
import plotly.graph_objects as go

def add_bar(i, y1, y2, color, data = loader):
    df = data.load_pickle(i)
    df = df[(df.year >= y1) & (df.year <= y2)]
    df_year = df.groupby(['year']).size().reset_index(name='count')
    new_bar = go.Bar(
                x = df_year.year.values,
                y = df_year['count'].values,
                name = 'data_'+ str(i),
                marker = {'color' : color})
    new_trend = go.Scatter(
                x = df_year.year.values,
                y = df_year['count'].values,
                mode="lines",
                line={'color' : color,
                    'width' : 0.5},
                showlegend=False)
    del df_year, df
    return new_bar, new_trend


def multi_barplot(year1, year2, colors):    
    # create a empty plotly.Figure object
    fig = go.Figure() 
    # compute the batch number
    n_batch = len(os.listdir('data'))
    # test the color list feed in argument
    # fit well with the batch number
    if n_batch > len(colors):
        raise Exception(
            "The colors list size({})doesn't ".format(len(colors)) +
            "fit with the number of data".format(n_batch))
    for i in range(1, n_batch + 1):
        fig.add_traces((add_bar(i, year1, year2, colors[i-1])))
    fig.update_layout(
        title = "Data distribution over years ({} - {})"
            .format(year1, year2),
        xaxis_title="years",
        yaxis_title="title",
        legend_title="Data batch")
    return fig


In [8]:
import plotly.colors as col

# create the color list
colors = col.qualitative.Plotly

# 1990 - 2023
fig1 = multi_barplot(1960, 1989, colors)
fig1.show()
# 1960 - 1990
fig2 = multi_barplot(1990, 2023, colors)
fig2.show()

The first bar chart (1960 - 1989) shows an increasing numbers of data over years. Moreover batch seems to have quite similar distriutions over years. data_1 and data_2 batch quite outperform the 4 others. data_6 batch is weaker than the other due to its poor number of rows.
The data behaves similarly until 2012 as we can see on the second chart (1990-2023). After this year there is great increasing of the data retrieved. A minimum increase of at least 100% of the batch can be observed. An increase of up to 50 times the batch size for some.

## Data pre-processing

The aim of this part is to preprocess data in order to get suitable data for the analysis. let's focus on the year variable.

We will focus on English songs, to facilitate the analysis and the work of natural language processing algorithms.

In [9]:
# Retrieve only the texts identified as English language by both cld3 and fasttext langid
df = df[df.language == 'en']

Next, it can be quite interseting to check Nan values

In [10]:
# find which column contain nan value
df.columns[df.isna().any()].tolist()

['title']

In [11]:
# get all rows that contain NaN values
df_nan = df[df.isna().any(axis=1)]
df_nan

title   tag                artist  year  views  \
114245   NaN  rock          Peter Dzubay  2017     52   
146772   NaN   rap                OLlama  2017   2120   
158344   NaN  rock  The Moth & The Flame  2011   1051   
160846   NaN  misc              Lawfermz  2017      3   
210243   NaN   rap        TripleYoThreat  2017     24   
211581   NaN   rap               Huntaps  2017    157   
294150   NaN   rap      Shaiza Maponyaza  2018     45   
309207   NaN  rock                  PAWS  2016    271   
357786   NaN   rap             J4ydizz1e  2018     55   
441948   NaN   rap          Bass Santana  2018   1147   
443704   NaN   rap           Poetic Mind  2018     43   
505748   NaN   rap                 KHANS  2018   1445   
584973   NaN  rock        Kathryn Joseph  2018    495   
619397   NaN   rap          Alex Micheal  2018     18   
643909   NaN   pop                 Kenia  2018     37   
670773   NaN   rap           Mehki Raine  2019    161   
671652   NaN  misc          Yoshi Flower  2018    115   
705033   NaN   pop         Matte SEXWAVE  2018     30   
805070   NaN   rap       Doxthe_maverick  2019     60   
991042   NaN    rb         YoungLamentar  2019     25   
992848   NaN   rap            Patagonist  2016     29   

                             features  \
114245                             {}   
146772                             {}   
158344                             {}   
160846                             {}   
210243                             {}   
211581                             {}   
294150                             {}   
309207                             {}   
357786                             {}   
441948  {"Kin\\$oul","Skott Summerz"}   
443704                             {}   
505748                             {}   
584973                             {}   
619397                             {}   
643909                             {}   
670773                             {}   
671652                             {}   
705033                   {"King Jaf"}   
805070                             {}   
991042                             {}   
992848                             {}   

                                                   lyrics       id  \
114245  When I finally find what's real, why shouldn't...  3166588   
146772  [Intro]\nToo many bitches; Too many bitches tr...  3210807   
158344  We used to be so similar\nWell that was wishfu...  3226446   
160846  (Intro)\nBeep beep beep beep beep beep.\nHello...  3230118   
210243  TripleYoThreat, you ain't never gonna make it\...  3296318   
211581  [Hook]\nFuck 12, if you fuck with me I'll send...  3297867   
294150  [intro]\n\nYah yah yah yah\nYah yah\nMan same ...  3438103   
309207  You're scared of history repeating on me\nCons...  3472732   
357786  [Intro: J4yDiZz1e]\n\nThis shit sounds just li...  3561848   
441948  [Intro: Bass Santana]\nTo Bass be the glory\nF...  3681585   
443704  [Verse 1: Exodu$]\n\nSee it started off when i...  3684185   
505748  Countdown to start...\n\n[Dialogue: "MOONLIGHT...  3777115   
584973  When the winter comes up\nSpring comes down\nW...  3890686   
619397  I can\nI can\nI can tell you how it be round h...  3939140   
643909  (verse 1)\nI try to know what I feel\nI`m stil...  3974045   
670773  [Verse 1]:\nI’m a soldier, man I love the atte...  4013370   
671652  [Interlude: Brandon Wardell]\nHey son, been li...  4014692   
705033  (Chorus) Matte SEXWAVE\n\nDon't be surprised w...  4065090   
805070  [Verse:]\n\nOhh God!\nLook they losing faith i...  4217064   
991042  But girl I love you, I can't kill myself\nStay...  4517608   
992848  Verse 1\n\nI love cyana\nShaniq teanna\nTaylor...  4520528   

       language_cld3 language_ft language  
114245            en          en       en  
146772            en          en       en  
158344            en          en       en  
160846            en          en       en  
210243            en          en       en  
211581            en          en       en  


In [12]:
print('Number of untitled song:', len(df[df.isna().any(axis=1)]))

Number of untitled song: 21


Insofar as the title of the music is not to be taken into account in the learning of the topic modeling algorithms but But the titles can be related to the topics in the next phase of analysis and the low number of songs without any title, I decide to delete this data for the moment.

In [13]:
# Delete rows containing NaN values
df = df.dropna()
len(df)

645573

Next, we also try to check for None values

In [14]:
df[df.isnull().any(axis=1)]

Empty DataFrame
Columns: [title, tag, artist, year, views, features, lyrics, id, language_cld3, language_ft, language]
Index: []

No None values in this dataframe.

Afterwards, let's look at the year variable, which is one of the important variables to take into account in our analysis because we want to extract the topics by decades.

In [15]:
years = df.year.unique()
print(years)

print('Number of unique years: ',len(years))

[2017 2016 1998 2002 2011 2013 2014 2015 2006 2009 2012 2005 2018 2008
 2003 2010 2007 1989 1986 1999 1905 1985 1994 2001 1899 1913 2000 2020
 1990 1984 1983 1979 2021 1995 2004 1825 1992 1993 2019 1980 1977 1966
 1988 1991 1997 1949 1957 1982 1674 1996 1974 1942 1850 1842    1 1964
 1972 1915 1976 1930 1987 1919 1911 1960 1978 1968 1975 1950 1981 1952
 1973 1951 1947 1954 1961 1892 1878 1934 1935 1970 1969 1944 1962 1909
 2022 1971 1927 1945 1936 1926 1938 1901   12 1900 1922 1929 1937 1953
 1820 1864 1965 1955 1540 1916 1963 1967 1918 1904 1943   14 1772 1788
 1780 1959 1886 1939 1871 1912 1956 1958 1880 1923 1910 1844 1897 1914
 1862 1933 1946   15 1877 1771   17 1948 1931 1898 1700 1888 1928  510
 1791 1895 1941 1920   25 1917 1908 1940 1859 1907 1902 2023 1857 1863
 1666 1893 1889 1861 1869 1925 1867 1872 1676 1675  420 1932  709 1818
 1830 1005 1866 1066  176 1300 1924 1251 1838 1760 1739   21 1758 1469
    2 1400 1853 1320 1200 1890 1860 1903   18 1220  130 1794 1896 1461
 1210 

We firstly want to know if the year variable format is suitable. It is highly likely that year are sometimes downsized (example : 92 instead of 1992).
Let's display the tag distribution for music with a release year below 215.

In [16]:
df_tag = df[df['year'] < 215].groupby(['tag']).size().reset_index(name='count')

fig = px.pie(df_tag, names="tag", values="count", title = "Outlier tag distribution")
fig.show()

It is rather surprising to observe that the majority style of music of this period (< 215) is rap music knowing that this style is known for the current emerging style. Of course, among this data their is a important part of outlier year.

In [17]:
# Extract the pieces of music of type 'rap' lower than the year 215
df_rap = df[(df['year'] < 215) & (df['tag'] == 'rap')]
df_rap.sort_values(by='views',ascending=False).head(20)

title  tag                      artist  \
111689                        Issa Snack  rap             Phatboitheceleb   
268205  Oof sandman sans sans diss track  rap                     Squeaky   
218600                    First Day Home  rap                       RetcH   
381769                              Papi  rap                DON-DON (US)   
715072                         Same Love  rap                  Macklemore   
969927          IWroteThisForTaylorSwift  rap                     Vershad   
268744                      I like frisk  rap                     Squeaky   
945081                    Same Lil Bitch  rap              Shayla Gessler   
18947              Dont Blame Me For You  rap             Kids These Days   
431118                           Robocop  rap             videogamedunkey   
871682              I don’t want another  rap                 $inbad (VA)   
720816                     Wont Back Out  rap          Flawless Real Talk   
151876                   The Race Keemix  rap                     Ayo Kee   
336793                       Tenxx Hours  rap                       Tenxx   
192002                              Kami  rap                      2burbo   
323357                             Sauce  rap  LilFlex (The one and only)   
200497             Dolce Lyrics Finished  rap                  Casper TNG   
731159                             Toast  rap    Guwop gumbo X Bando Beej   
189766                  Pimpin Aint Easy  rap               Jackie B (IL)   
438752   Break Your Fucking Neck Part. 2  rap                      YungQC   

        year  views                                           features  \
111689     1   4182                                                 {}   
268205    15   3206                                                 {}   
218600     1   2334                                                 {}   
381769     1   2129                                                 {}   
715072     1   1767                        {"Macklemore & Ryan Lewis"}   
969927     1   1607                                   {"Brooklyn Zoo"}   
268744     1   1186                                     {"Squeaky jr"}   
945081     1   1023                                                 {}   
18947      1    868    {"VIC MENSA","Macie Stewart","Liam Cunningham"}   
431118     1    766                                 {​videogamedunkey}   
871682     1    669                                  {"\\$inbad (VA)"}   
720816     1    669                                            {Freek}   
151876     1    543                                                 {}   
336793     1    416                                                 {}   
192002    17    415                                                 {}   
323357     1    400                                          {3rdKvng}   
200497     1    357                                                 {}   
731159     1    336  {"Guwop gumbo ft Bando Beej","Guwop gumbo X  B...   
189766     1    309                                                 {}   
438752     1    307                                                 {}   

                                                   lyrics       id  \
111689  Chorus: its ya birthday and you know I ain't f...  3163216   
268205  OOF POOF BOOTH LOSE LOOSE MOVE LUKE FRISK WRIS...  3387617   
218600  [Intro]\n\n[Chorus]\nHome, it's my first day h...  3307004   
381769  [INTRO]\nCall me papi\nCall me papi\nLead her\...  3596060   
715072  When I was in the 3rd grade\nI thought that I ...  4080328   
969927  [Intro]\nJake:  Sounds like your sad. Listen, ...  4484444   
268744  Ok, ok, ok, ok, ok, ok, ok, yeah\nI like frisk...  3388825   
945081  Did me dirty, you been fuckin' with the Same L...  4441966   
18947   [Verse 1: Vic Mensa]\nI'm larger than life, ha...  3044399   
431118  Now that I'm a Robocop\n\nNow I'm never gonna ...  3666068   
871682  (Hook)\n\nI'm Cold hearted, And broke/\nI cold...  4323086   
720816  [Intro - Flawl

In [18]:
df_rap[df_rap['artist'] == 'Kanye East']

Empty DataFrame
Columns: [title, tag, artist, year, views, features, lyrics, id, language_cld3, language_ft, language]
Index: []

If we search the release date of this track on google, we can find a release date from 4 May 2021 on the [Genius website](https://genius.com/Kanye-east-the-secrets-of-dababy-lyrics). Given the year that we find in our table and real one, we can assume some issue about the date format (1 instead 2021).

After few research on genius website, the most viewed songs of this above displayed list seems to be released on 2021 but more views decrease harder is the interpretation of date.

Let's check the second most popular tag 'pop' in this retrieve outliers data :

In [19]:
# Extract the pieces of music of type 'rap' lower than the year 215
df_pop = df[(df['year'] < 215) & (df['tag'] == 'pop')]
df_pop.sort_values(by='views',ascending=False).head(20)

title  tag  \
274779                                      Off White  pop   
951623             I dont wanna see you cryin anymore  pop   
495830                       Hello from the Dark Side  pop   
385856                            The Moons Detriment  pop   
635909                             Mostly to Yourself  pop   
433617                                 Come September  pop   
599147                                           Gone  pop   
433630                         The Pursewarden Affair  pop   
318347                                       The Rose  pop   
918072         U cut me off so the cuts r on me now..  pop   
37439                                          Noirse  pop   
879213  Fadl Shaker - Allah Aalam English Translation  pop   
939993                                Nana Rose Remix  pop   
367980            I’m Working on a Road to Glory Land  pop   
949859                                        Freddie  pop   
860863                                         So Low  pop   
991033                                   Take Me Back  pop   
871246                                    Dear Father  pop   
569400                                          Ghost  pop   
644307                                     1000 years  pop   

                             artist  year  views              features  \
274779                 Zach Clayton     1   7894                    {}   
951623                 Adam Melchor     1   7479                    {}   
495830              RoyishGoodLooks    15   7019                    {}   
385856                  Shannon Lay     1   6698                    {}   
635909                    Noah Reid     1   3517                    {}   
433617                Anas Mitchell     1   1244    {"Anaïs Mitchell"}   
599147                 Ella Martine     1    946                    {}   
433630                Anas Mitchell     1    732    {"Anaïs Mitchell"}   
318347                 Common Holly     1    642                    {}   
918072                 Sapphire2001     1    495                    {}   
37439                   Petite Noir    14    461                    {}   
879213  Genius English Translations     1    383                    {}   
939993                     Big kris     1    278                    {}   
367980       The Earls of Leicester     1    266                    {}   
949859                   Ella Clair     1    265                    {}   
860863                Cinematic Pop     1    264     {"Spencer Jones"}   
991033                       Mcrack     1    245                    {}   
871246                 Laura Bretan     1    229                    {}   
569400                       PYNKIE    12    161                    {}   
644307                 Joel McNeely     1    143  {"KT Tunstall",Bleu}   

                                                   lyrics       id  \
274779  Chorus\nSwish on my kicks, off white\nStripes ...  3399877   
951623  [Verse 1]\nI don't wanna see you cryin’ anymor...  4452665   
495830  [Chorus]\nHello from the Dark Side\nI must've ...  3763085   
385856  If I were to know you\nI’d show you all the li...  3603840   
635909  Well it's mostly in the mornin'\nWhen your eye...  3961929   
433617  Autumn's ashes, summer's embers\nOn the sidewa...  3669873   
599147  [Verse 1]\nIt's hard we hurt each other\nTime ...  3910616   
433630  Percy Pursewarden\nOpen up your door\nI haven'...  3669885   
318347  Well I know I was the rose\nBut now I feel lik...  3496110   
918072  I can feel in the air tonight\nSmoke seeping f...  4401036   
37439   Show me your secret\nLet's have a party\nShow ...  3067334   
879213  Only god knows, if I was dreaming, my darling\...  4334911   
939993  90 years old, it's not young but\nGod broke th...  4434139   
367980  [Chorus]\nI’m Working on a road that leads to ...  3576520   
949859  [Verse 1]\nWell Freddie said my life is really...  4449344   
860863  Have you ever been so low?\nYes you had a hear...  4306998   


The titles recovered seem to be for the most part recent sounds, not very popular with a bad indexation of the years.

A case-by-case pre-processing of the data is too tedious compared to the amount of data to be processed. We will only use data with correctly formatted dates.

In [20]:
df = df[(df.year >= 1960) & (df.year < 2023)]
len(df)

642975

We wish to analyze the texts by decade then let's add a decade column.

In [21]:
import math

df['decade'] = df['year'].map(lambda x : int(math.trunc(x / 10) * 10))

df.sort_values(by = 'year').head(20)

title   tag          artist  \
329044                             Darling If I Had You  rock       Bobby Day   
734933  Tonights All Right For Love Bonus Track Version   pop   Elvis Presley   
752292                                    Row Your Boat   pop   The Chipmunks   
374556                      Two Views of a Cadaver Room  misc    Sylvia Plath   
374557                                     The Eye-Mote  misc    Sylvia Plath   
7170                           Extra Sensory Perception   pop  Sheldon Allman   
374558                                 Hardcastle Crags  misc    Sylvia Plath   
374559                                             Faun  misc    Sylvia Plath   
479255                                        Whirlwind    rb  Barrett Strong   
374560                                        Departure  misc    Sylvia Plath   
655765                                  Show Me the Way   pop     Ben E. King   
752290                          Working on the Railroad   pop   The Chipmunks   
752289                          Swing Low Sweet Chariot   pop   The Chipmunks   
752288                                Sing a Goofy Song   pop   The Chipmunks   
752286                  When Johnny Comes Marching Home   pop   The Chipmunks   
752285                                     Swanee River   pop   The Chipmunks   
752284                             I Wish I Had a Horse   pop   The Chipmunks   
374561                                          Lorelei  misc    Sylvia Plath   
752283                                Home on the Range   pop   The Chipmunks   
774932                                    How About Me?   pop    Julie London   

        year  views               features  \
329044  1960    308                     {}   
734933  1960    142                     {}   
752292  1960    261                     {}   
374556  1960   1079                     {}   
374557  1960    453                     {}   
7170    1960    193                     {}   
374558  1960    266                     {}   
374559  1960    329                     {}   
479255  1960    109  {"The Rayber Voices"}   
374560  1960    375                     {}   
655765  1960    707                     {}   
752290  1960     96                     {}   
752289  1960     65                     {}   
752288  1960    201                     {}   
752286  1960    126                     {}   
752285  1960     67                     {}   
752284  1960    304                     {}   
374561  1960    343                     {}   
752283  1960    186                     {}   
774932  1960     58                     {}   

                                                   lyrics       id  \
329044  Darling if I had you, if I had you\nMmh, what ...  3515784   
734933  Hold me tight the moon's so bright\nTonight th...  4111118   
752292  Careful now, fellas, steady\nDon't tip it over...  4136301   
374556  (1)\nThe day she visited the dissecting room\n...  3585530   
374557  Blameless as daylight I stood looking\nAt a fi...  3585531   
7170    We've got extra sensory perception\nIt makes o...  3029810   
374558  Flintlike, her feet struck\nSuch a racket of e...  3585532   
374559  Haunched like a faun, he hooed\nFrom grove of ...  3585533   
479255  You know it hit me (Hit me like whirlwind)\nYo...  3738355   
374560  The figs on the fig tree in the yard are green...  3585534   
655765  [Verse 1]\nIf I had to swim a river\nOr climb ...  3990976   
752290  Ouch!\nOh, careful Simon!\nOw!\nLook where you...  4136300   
752289  Swing low, sweet chariot\nComing for to carry ...  4136299   
752288  Sing a goofy song as you walk along\nRee dee d...  4136298   
752286  Alvin, Simon, Theodore!\nReady?\nMarch!\n\nWhe...  4136296   
752285  Boys, how would ya like to do something southe...  4136295   
752284  Hey guys, how come you're rubbing a rabbit's f...  4136294   
374561  It is no night to drown in:\nA full moon, rive...  3585535   
752283  Ooo\nOh, give me a home where the buffalo r

## Data vizualisation

Let's do some vizualisation to get a better understanding of our data. As we saw on previous distribution graphs over years, more titles have been recorded over the last 2 decades.

In [22]:
# barplot by decade
def barplot_by_decade(df):

    # groupby decade
    df_d = df.groupby(['decade']).size().reset_index(name='count')

    # create the figure
    fig = go.Figure()

    fig.add_bar(
        x=df_d.decade,
        y=df_d['count'],
        showlegend=False)

    fig.add_scatter(
            x=df_d.decade,
            y=df_d["count"],
            mode="markers+lines",
            name="trend",
            showlegend=False)

    fig.update_layout(
            title = "Music release over years",
            xaxis_title="decade",
            yaxis_title="release")
    return fig

# build and display
fig = barplot_by_decade(df)
fig.show()

In [23]:
# compute tag frequencies by decade
df_pies_d = df.groupby(['decade','tag']).size().reset_index(name='count')
df_pies_d[df_pies_d.decade == 1960]

decade      tag  count
0    1960  country    764
1    1960     misc    271
2    1960      pop   2292
3    1960      rap      8
4    1960       rb    704
5    1960     rock    688

In [24]:
from plotly.subplots import make_subplots

# create en make subplot
fig = make_subplots(rows=3, cols=3,
                    specs=[
                        [{'type':'domain'}
                        for i in range(1,4)] for i in range(1,4)
                    ])
decades = df_pies_d.decade.unique().tolist()
for i in range(0,3):
    for k in range(0,3):
        decade = decades[i*3 + k]
        # group by decade
        df_p = df_pies_d[df_pies_d.decade == decade]
        # add figure
        fig.add_trace(go.Pie(labels=df_p.tag, values=df_p['count'], name=decade), i+1, k+1)
        # add annotation
        fig.add_annotation(arg=dict(
            text=decade, x=k*0.375 + 0.125,
            y=-i*0.3927 + 0.90, font_size=10,
            showarrow=False))
        if (i*3 + k) == 6:
            break


# Use `hole` to create a donut-like pie chart
fig.update_traces(hole=.4, hoverinfo="label+percent+name")

fig.update_layout(
    title_text="Tags proportions by decades"
    # Add annotations in the center of the donut pies.
    #annotations=[dict(text=decade, x=k*0.375+0.125, y= -i*0.125+0.90, font_size=10, showarrow=False)
     #           for k, decade in enumerate(decades) for i in range(0,4)]
)
fig.show()

The different pie charts show us an evolution of the different proportions of music styles by decades from 1960 to today. In the sixties the most listed music style is the **pop music**. Then comes an emergence of a rising style: the **rock**. This one increases with the decades until it overtakes the pop music during the decades 90 and 2000. The two styles come to balance thereafter facing the meteoric rise of the most listed genre in our current decade, namely **rap**. The evolution of the proportions recover can give us a rather precise idea of the most popular styles of their times. However, it is important to remember that the data still has some bias, Genius being a crowdsourced tool created during the last decade and at the base only as a lexical translator of rap music, it is normal to find a large amount of data from this period and especially from this style there.

The different pie charts show us an evolution of the different proportions of music styles by decades from 1960 to today. In the sixties the most listed music style is the **pop music**. Then comes an emergence of a rising style: the **rock**. This one increases with the decades until it overtakes the pop music during the decades 90 and 2000. The two styles come to balance thereafter facing the meteoric rise of the most listed genre in our current decade, namely **rap**. The evolution of the proportions recover can give us a rather precise idea of the most popular styles of their times. However, it is important to remember that the data still has some bias, Genius being a crowdsourced tool created during the last decade and at the base only as a lexical translator of rap music, it is normal to find a large amount of data from this period and especially from this style there.## Text preprocessing

After the visualisation part let's focus more on the main data which are the lyrics.

In [25]:
df.iloc[0]["lyrics"]

"The roses start to wither\nWhere the devil lays to sleep\nAnd sorrow seems to be like joy\nWhere dying lights dance on last time\n\nYou had me at hello\nBut I couldn't see right through your twisted soul\nThis was the downfall of us all\n\n(Roses start to wither\nWhere the devil lays to sleep)\n\nToo close to hell\nI can't see\nWhat ate me up from the inside\nToo close to hell\nI will never see\nWhat ate me up from the inside out\n(From the inside out)\n\nI'm caught in a nightmare\nNo chance to make it out alive\nWhy have we left the place\nWhere we found love\nYou had me at hello\nBut I couldn't see right through your twisted soul\nThis was the downfall of us all\n\n(Roses start to wither\nWhere the devil lays to sleep)\n\nToo close to hell\nI can't see\nWhat ate me up from the inside\nToo close to hell\nI will never see\nWhat ate me up from the inside out\n\nSo sing along\nWe are a battle\nSo sing along\nWhy have you forsaken me?\n\nWhy have you forsaken me?\nWhy have you forsaken m

There is many undesirable characters like the line breaker '\n', figures or square, curly and simple brackets. So let's clean this data with regular expressions.

In [26]:
import re
from numpy.random import randint

def clean_text(text):
    # remove \n
    text = text.replace('\n', ' ')
    # remove punctuation
    text = re.sub(r'[,\.!?]', '', text)
    #removing text in square braquet
    text = re.sub(r'\[.*?\]', ' ', text)
    #removing numbers
    text = re.sub(r'\w*\d\w*',' ', text)
    #removing bracket
    text = re.sub(r'[()]', ' ', text)
    # convert all words in lower case
    text = text.lower()
    return text

# get the results of data cleaning
cleaned_text = df["lyrics"].apply(clean_text)

In [27]:
docs = cleaned_text.to_list()
docs[0]

"the roses start to wither where the devil lays to sleep and sorrow seems to be like joy where dying lights dance on last time  you had me at hello but i couldn't see right through your twisted soul this was the downfall of us all   roses start to wither where the devil lays to sleep   too close to hell i can't see what ate me up from the inside too close to hell i will never see what ate me up from the inside out  from the inside out   i'm caught in a nightmare no chance to make it out alive why have we left the place where we found love you had me at hello but i couldn't see right through your twisted soul this was the downfall of us all   roses start to wither where the devil lays to sleep   too close to hell i can't see what ate me up from the inside too close to hell i will never see what ate me up from the inside out  so sing along we are a battle so sing along why have you forsaken me  why have you forsaken me why have you forsaken me why have you forsaken me why have you forsak

In [28]:
# update dataframe
df.update(cleaned_text)
df.head(3)

title   tag        artist  year  views               features  \
0           Roses  rock         Vitja  2017    399                     {}   
1  Keep On Pushin   rap       Problem  2017    692  {"My Princess Aeryn"}   
2          Inside   pop  The jepettos  2017   1302                     {}   

                                              lyrics       id language_cld3  \
0  the roses start to wither where the devil lays...  3019113            en   
1    imma keep on pushin imma keep on pushin stay...  3019114            en   
2    ooh ooh ah ah        i heard you were the wo...  3019115            en   

  language_ft language  decade  
0          en       en    2010  
1          en       en    2010  
2          en       en    2010

That's better! The libraries that we will use later to perform topic modeling usually provide preprocessing but it is always good to have control over what we manipulate.

## Topic modeling

I will perform 2 ways to do topic modeling :
- [LDA (latent dirichlet allocation)](https://fr.wikipedia.org/wiki/Allocation_de_Dirichlet_latente) are the common way to do topic modeling in the few last years, it works and it's quite easy to use with common python library like [Gensim](https://radimrehurek.com/gensim/auto_examples/index.html).
- [BERTopic](https://maartengr.github.io/BERTopic/index.html) seems to be one of the best technic this day to perform topic modeling. It combine the leverage of [BERT](https://en.wikipedia.org/wiki/BERT_(language_model)) the famous language model with [c-TF-IDF](https://maartengr.github.io/BERTopic/api/ctfidf.html) tansformer. 


### Define default tokenizer and Lemmatizer

In [29]:
import spacy

print("set gpu: ", spacy.prefer_gpu())

# small model /!\ take the bigger one for Kaggle
new_nlp = spacy.load('en_core_web_sm')

set gpu:  False


It could be difficult to process all this data on my computer or Kaggle. The memory will quickly be overwhelmed. I will work with a sample of our previously load data in order to avoid memory overload.

In [30]:
from collections import Counter

def sample(balanced = True, data = df, prop = 0.1):
    if balanced:
        # compute the sorted decreasing parties frequencies
        decade_frequencies = Counter(data['decade']).most_common()
        print(decade_frequencies)

        # retrieve the under represented class
        nb_under_class = decade_frequencies[-1][1]

        # Return a random sample of items from each party following the under sampled number of class
        sample_df = data.groupby("decade").sample(n = nb_under_class, random_state = 500)
    else:
        # create sample df 1/3 of the actual loaded data
        sample_df = df.sample(frac = prop)
    return sample_df
        

In [31]:
# sample the data
sdf = sample()

[(2010, 571574), (2000, 33998), (1990, 14189), (1980, 8788), (1970, 7088), (1960, 4727), (2020, 2611)]


In [32]:
# check the distribution of the sample
barplot_by_decade(sdf)

In [33]:
# default preprocessing
def preprocess(text, nlp = new_nlp):

    #TOKENISATION
    tokens =[]
    for token in nlp(text):
        tokens.append(token)

    #REMOVING STOP WORDS
    spacy_stopwords = new_nlp.Defaults.stop_words
    sentence =  [word for word in tokens if word.text.isalpha() and word.text not in spacy_stopwords]

    #LEMMATISATION
    sentence = [word.lemma_ for word in sentence]

    return sentence

### Vizualise most frequent words over decades

In [34]:
from tqdm import tqdm
from sklearn.feature_extraction.text import CountVectorizer

class TermsDocumentsMatrix():
    
    def __init__(self, sdf, decades=[1960, 1970], colorscale = 'Plotly3'):
        # vectorizer on the sample lyrics
        self.__vectorizer = CountVectorizer(tokenizer = preprocess)
        # fit and transform the data
        self.__data_vectorized = self.__vectorizer.fit_transform(
            tqdm(sdf['lyrics'].loc[sdf['decade'].isin(decades)])
        )
        # get decades informations
        self.__decades = sdf['decade'].loc[sdf['decade'].isin(decades)].reset_index(drop=True)
        self.__unique_decades = decades
        # get colorscale template
        self.__colorscale = colorscale
    
    def get_tdmatrix(self):
        
        # compute a Matrix terms document by decades
        df_bw = pd.DataFrame(self.__data_vectorized.toarray(),
                    columns = self.__vectorizer.get_feature_names_out())
        
        # check the length
        if len(df_bw) != len(self.__decades):
            raise Exception('Not the same size')
        
        # concatenate decade
        df_bw['decade'] = self.__decades
        
        # check NaN values
        if len(df_bw.columns[df_bw.isna().any()].tolist()) != 0:
            raise Exception('Decade got Nan values')

        return df_bw
    
    def get_tdm_by_decade(self, decade):
        
        if decade not in self.__unique_decades:
            raise Exception("{} doesn't appear in the decades list".format(decade))
        
        # compute a Matrix terms document by decades (bag of words format)
        df_bw = pd.DataFrame(self.__data_vectorized.toarray(),
                    columns = self.__vectorizer.get_feature_names_out())
        
        # check the length
        if len(df_bw) != len(self.__decades):
            raise Exception('Not the same size')
        
        # concatenate decade
        df_bw['decade'] = self.__decades
        
        # check NaN values
        if len(df_bw.columns[df_bw.isna().any()].tolist()) != 0:
            raise Exception('Decade got Nan values')
        
        # select suitable decade
        df_bw = df_bw[df_bw['decade'] == decade]
        
        return df_bw
    
    def most_freq_terms(self, n_rows = 1, n_cols = 2, n_terms = 10):
        
        # create the document terms matrix
        df_bw = self.get_tdmatrix()
        
        # create en make subplot
        fig = make_subplots(rows=n_rows, cols=n_cols,
                            x_title = 'number of occurrences',
                            y_title = 'terms',
                            subplot_titles = self.__unique_decades)
        
        for i in range(0,n_rows):
            for k in range(0,n_cols):
                if (i*n_rows + k) == len(self.__unique_decades):
                    break
                
                # get the decade
                decade = self.__unique_decades[i*n_rows + k]
            
                #select the suitable decade and delete decade column
                df_decade = df_bw.loc[df_bw.decade == decade, df_bw.columns != 'decade']
                
                # compute terms frequencies by decade
                terms_freq = df_decade.sum().sort_values(ascending = False)
            
                # total number of terms occurences
                total_terms = terms_freq.values
                
                # add figure
                fig.add_trace(go.Bar(y=terms_freq.index.tolist()[:n_terms][::-1],
                                     x=total_terms[:n_terms][::-1],
                                     name=decade,
                                     orientation='h', showlegend = False,
                                    marker = dict(color = total_terms,
                                                  colorscale=self.__colorscale)),
                              i+1, k+1)
        return fig

In [35]:
# first decades
tdm = TermsDocumentsMatrix(sdf, decades = [1960, 1970, 1980, 1990],
                           colorscale = 'Plasma')

# display bar charts of most frequent terms
tdm.most_freq_terms(n_rows = 2, n_cols = 2, n_terms = 15)

100%|██████████| 10444/10444 [05:49<00:00, 29.85it/s]


According to the bar graphs displayed above, a group of words seems to recur on each decade: Love, know, go, feel ... Words that seem to relate to the popular song that can talk about love. This is consistent with our previous analysis from the pie charts showing the proportions of musical styles across time. We also notice an important presence of onomatopoeia like yeah or oh.

In [36]:
# first decades
tdm = TermsDocumentsMatrix(sdf, decades = [2000, 2010, 2020],
                          colorscale = 'Plasma')

# most frequent terms
tdm.most_freq_terms(n_rows = 2, n_cols = 2, n_terms = 15)

100%|██████████| 7833/7833 [05:18<00:00, 24.63it/s]


We get similar results on this second decade with similar high occurrence words. We see a greater amount of onomatopoeia in the current decade. We can explain this by an emergence of the rap music style on this current and last decade. There is in this style of music a very used process, the 'ad-libs'. They are sounds, words or onomatopoeias that the artists pronounce sometimes between two verses or at the end of a sentence to give more impact to their text and to dynamize the atmosphere of a title. This may explain the greater presence of onomatopoeia in the lyrics of this decade.


### Topic modeling with LDA

LDA is a common technic use in topic modeling, we firstly process basic preprocessing.

In [37]:
# gensim
from gensim.models import CoherenceModel
from gensim.models.ldamodel import LdaModel
from gensim.models.ldamulticore import LdaMulticore
from gensim.corpora.dictionary import Dictionary
from gensim.test.utils import datapath

# utils
from datetime import datetime
import logging

# dashboards
import pyLDAvis
import pyLDAvis.gensim
import matplotlib.pyplot as plt

# TSNE dependencies
from sklearn.manifold import TSNE
from bokeh.plotting import figure, output_file, show
from bokeh.models import Label
from bokeh.io import output_notebook
import numpy as np
import matplotlib.colors as mcolors

#gensim_log = '/kaggle/working/log/gensim.log'

#initiate log file
#logging.basicConfig(filename=gensim_log,
#                   format='%(asctime)s:%(levelname)s:%(message)s',
#                    level=logging.INFO,
#                   force = True)

# utils
def parse_logfile(path_log):
    matcher = re.compile(r'(-*\d+\.\d+) per-word .* (\d+\.\d+) perplexity')
    likelihoods = []
    with open(path_log) as source:
        for line in source:
            match = matcher.search(line)
            if match:
                likelihoods.append(float(match.group(1)))
    return likelihoods


class LDATopicModeling():
    
    def __init__(self, df = sdf,
                 decade = 1960,
                 directory = "/kaggle/working/models/",
                 existing = False,
                 n_topics = 10,
                 worker_nodes = None,
                lang_preprocess = preprocess,
                cross_valid = False,
                epochs = 30):
        # Apply preprocessing on decade data
        self.__documents = df.loc[df.decade == decade, 'lyrics'].apply(lang_preprocess)
            
        # Create a corpus from a list of texts
        self.__id2word = Dictionary(self.__documents.tolist())
        self.__corpus = [self.__id2word.doc2bow(doc) for doc in self.__documents.tolist()]
        
        #training
        if os.path.isfile(existing):
            # Load a potentially pretrained model from disk.
            self.model = LdaModel.load(temp_file)
            self.__cv_results = None # no cross_valid
            self.__n_topics = n_topics
        elif not cross_valid:
            self.model = LdaMulticore(
                corpus=tqdm(self.__corpus),
                id2word=self.__id2word,
                num_topics=n_topics,
                workers=worker_nodes,
                passes=epochs)
            self.__n_topics = n_topics
            self.__cv_results = None
        else: # cross validation
            
            # hyperparameter
            alpha = []#np.arange(0.01, 1, 0.3).tolist()
            alpha.append('symmetric')
            alpha.append('asymmetric')
            
            # hyperparameter
            eta = []#np.arange(0.01, 1, 0.3).tolist()
            eta.append('symmetric')
            
            # compute results of the cross_validation
            cv_results = {
                 'topics': [],
                 'alpha': [],
                 'eta': [],
                 'coherence': []
            }
            
            # topic range
            topic_range = range(2, n_topics+1)
            
            # prevent the computation time
            total=(len(eta)*len(alpha)*len(topic_range))
            print("total lda computation: ",total)
            model_list = []
            
            for k in topic_range:
                for a in alpha:
                    for e in eta:
                        
                        # train the model
                        model = LdaMulticore(
                            corpus=self.__corpus,
                            id2word=self.__id2word,
                            num_topics=k,
                            workers=worker_nodes,
                            passes=epochs,
                            alpha=a,
                            eta=e)
                        
                        # compute coherence
                        cv = CoherenceModel(
                            model=model,
                            texts=self.__documents,
                            dictionary=self.__id2word,
                            coherence='c_v')
                        
                        print('coherence: {}\nalpha: {}\neta: {}\ntopic: {}'.format(
                            cv.get_coherence(), a, e, k))
                        
                         # Save the model results
                        cv_results['topics'].append(k)
                        cv_results['alpha'].append(a)
                        cv_results['eta'].append(e)
                        cv_results['coherence'].append(cv.get_coherence())
                        model_list.append(model)
            # retrieve index of the highest coherence model
            best_index = np.argmax(cv_results['coherence'])
            
            # choose the model given the best coherence
            self.model = model_list[best_index]
            
            # save results as attribute
            self.__cv_results = cv_results
            
            self.__n_topics = cv_results['topics'][best_index]
                                    
            # logging doesn't work on Kaggle
            #self.__likelihood = parse_logfile()
        # directory path
        self.__directory = directory
    
    # getters
    @property
    def get_id2word(self):
        return self.__id2word
    
    @property
    def get_corpus(self):
        return self.__corpus
    
    @property
    def get_likelihood(self):
        return self.__likelihood
    
    @property
    def get_cv_results(self):
        return pd.DataFrame(self.__cv_results) if self.__cv_results else None
    
    def plot_coherence(self, metric = 'alpha'):
        """metric(str): alpha or eta
        """
        if self.__cv_results is None:
            raise Exception('No cross validation available')
        
        # get the dataframe
        df_res = self.get_cv_results
                                    
        # groupby by metric
        grouped = df_res.groupby(metric)
        # create the layout
        fig = go.Figure()
        for level, df in grouped:
            fig.add_trace(
                go.Scatter(
                    x=df.topics,
                    y=df.coherence,
                    mode='lines+markers',
                    name=str(level)
                )
            )
        fig.update_layout(
            title = "coherence over topics by",
            xaxis_title="topic",
            yaxis_title="coherence")
        return fig
                                    
                                    
    def save_current_model(self):
        # retrieve time
        now = datetime.now()
        # create the directory if it doesn't exist
        try:
            os.makedirs(directory + now.strftime("%d%m%Y_%H%M%S"))
        except:
            pass
        # Save model to disk.
        temp_file = datapath(directory + now.strftime("%d%m%Y_%H%M%S") + '/model')
        
        self.model.save(temp_file)

    def get_perplexity(self):
        return self.model.log_perplexity(self.__corpus)
    
    def get_coherence(self):
        coherence_model_lda = CoherenceModel(
            model=self.model,
            texts=self.__documents,
            dictionary=self.__id2word,
            coherence='c_v')
        return coherence_model_lda.get_coherence()
    
    
    # data vizualisation
    def dashboard_LDAvis(self):
        # some basic dataviz
        pyLDAvis.enable_notebook()
        vis = pyLDAvis.gensim.prepare(self.model, self.__corpus,
                                      dictionary = self.model.id2word)
        return vis
        
    def plot_tsne(self):
        # n-1 rows each is a vector with i-1 posisitons, where n the number of documents
        # i the topic number and tmp[i] = probability of topic i
        topic_weights = []
        for row_list in self.model[self.get_corpus]:
            tmp = np.zeros(self.__n_topics)
            for i, w in row_list:
                tmp[i] = w
            topic_weights.append(tmp)


        # Array of topic weights    
        arr = pd.DataFrame(topic_weights).fillna(0).values

        # Keep the well separated points (optional)
        arr = arr[np.amax(arr, axis=1) > 0.35]

        # Dominant topic number in each doc
        topic_num = np.argmax(arr, axis=1)

        # tSNE Dimension Reduction
        tsne_model = TSNE(n_components=2, verbose=1, init='pca')
        tsne_lda = tsne_model.fit_transform(arr)

        # Plot the Topic Clusters using Bokeh
        output_notebook()
        mycolors = np.array([color for name, color in mcolors.TABLEAU_COLORS.items()])
        plot = figure(title="t-SNE Clustering of {} LDA Topics".format(self.__n_topics), 
                      plot_width=900, plot_height=700)
        plot.scatter(x=tsne_lda[:,0], y=tsne_lda[:,1], color=mycolors[topic_num])
        show(plot)
        
    def plot_likelihood(self):
        fig = go.Figure(
            go.Scatter(x=[range(0,50)], y=self.__likelihood[-50:],
                       mode='lines',
                       name='lines'))
        fig.update_layout(
            title = "Likelihood over passes",
            xaxis_title="Likekihood",
            yaxis_title="passes")
        return fig

In [38]:
# create my model
lda_model = LDATopicModeling()

100%|██████████| 2611/2611 [00:00<00:00, 13485.54it/s]


In [39]:
# print the result
lda_model.model.print_topics()

[(0,
  '0.019*"people" + 0.013*"know" + 0.010*"get" + 0.010*"man" + 0.009*"rock" + 0.008*"go" + 0.008*"black" + 0.007*"white" + 0.006*"country" + 0.006*"come"'),
 (1,
  '0.065*"love" + 0.033*"know" + 0.030*"baby" + 0.019*"go" + 0.018*"get" + 0.016*"oh" + 0.016*"time" + 0.014*"heart" + 0.014*"way" + 0.013*"come"'),
 (2,
  '0.022*"doo" + 0.017*"da" + 0.010*"chain" + 0.009*"glory" + 0.008*"high" + 0.008*"sing" + 0.008*"hey" + 0.008*"like" + 0.007*"sunday" + 0.006*"whoa"'),
 (3,
  '0.072*"oh" + 0.036*"baby" + 0.032*"want" + 0.031*"yeah" + 0.030*"love" + 0.029*"little" + 0.019*"know" + 0.015*"come" + 0.014*"tell" + 0.014*"girl"'),
 (4,
  '0.016*"say" + 0.011*"jem" + 0.007*"black" + 0.007*"think" + 0.007*"like" + 0.007*"come" + 0.006*"look" + 0.006*"know" + 0.006*"house" + 0.006*"dill"'),
 (5,
  '0.038*"man" + 0.031*"home" + 0.018*"like" + 0.017*"girl" + 0.011*"go" + 0.010*"little" + 0.009*"sun" + 0.009*"run" + 0.008*"get" + 0.008*"mind"'),
 (6,
  '0.026*"come" + 0.016*"alright" + 0.015*"hey

In [40]:
lda_model.plot_tsne()

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2555 samples in 0.002s...
[t-SNE] Computed neighbors for 2555 samples in 0.120s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2555
[t-SNE] Computed conditional probabilities for sample 2000 / 2555
[t-SNE] Computed conditional probabilities for sample 2555 / 2555
[t-SNE] Mean sigma: 0.001948


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] KL divergence after 250 iterations with early exaggeration: 66.294144
[t-SNE] KL divergence after 1000 iterations: 0.595812


Loading BokehJS ...

In [41]:
lda_model.dashboard_LDAvis()

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
1     -0.182280  0.024772       1        1  33.466224
9      0.005800 -0.075752       2        1  13.902044
3     -0.184647  0.064976       3        1  10.054218
4      0.094625  0.009101       4        1   9.606449
5      0.011091  0.018172       5        1   7.714627
0      0.117516  0.098820       6        1   5.461407
7      0.092430 -0.010099       7        1   5.122596
8      0.069276  0.118886       8        1   4.919579
6     -0.076203 -0.077870       9        1   4.896056
2      0.052394 -0.171006      10        1   4.856801, topic_info=      Term         Freq        Total Category  logprob  loglift
32      oh  3229.000000  3229.000000  Default  30.0000  30.0000
16    baby  3232.000000  3232.000000  Default  29.0000  29.0000
8     love  6070.000000  6070.000000  Default  28.0000  28.0000
613     la   737.000000   737.000000  Default  27.0000  27.0000
13    yeah  1926.000000  1926.000000  Default  26.0000  26.0000
..     ...          ...          ...      ...      ...      ...
363  round    44.426328   272.781054  Topic10  -5.5220   1.2100
8     love    51.223790  6070.556936  Topic10  -5.3796  -1.7502
140    say    47.002905  1426.012500  Topic10  -5.4656  -0.3876
28     let    46.875413  1448.562126  Topic10  -5.4683  -0.4060
197   tell    46.325998  1566.011827  Topic10  -5.4801  -0.4958

[756 rows x 6 columns], token_table=       Topic      Freq     Term
term                           
2699       9  0.879084    abide
12046      5  0.935922  abilene
1613       1  0.116320   affair
1613       2  0.019387   affair
1613       3  0.717305   affair
...      ...       ...      ...
733        7  0.061603    young
733        8  0.025668    young
733        9  0.010267    young
733       10  0.107806    young
4897       8  0.962069     zone

[2379 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[2, 10, 4, 5, 6, 1, 8, 9, 7, 3])

Let's perform lda for each decade.

In [42]:
# LDA Topic Modeling by decade
class LDAPipeline():
    
    def __init__(self,
                 prep = preprocess,
                 cv = False,
                 decades = [
        1960, 1970, 1980, 1990, 2000, 2010, 2020
    ]):
        self.models = {
            decade : LDATopicModeling(
                decade = decade,
                lang_preprocess = prep,
                epochs = 10,
                cross_valid = cv) for decade in decades}
        
    def get_metrics(self):
        # compute metrics
        metrics = {
                 'decade': [],
                 'coherence': [],
                 'perplexity': []
        }
        for decade, model in self.models.items():
            metrics['decade'].append(decade)
            metrics['coherence'].append(model.get_coherence())
            metrics['perplexity'].append(model.get_perplexity())
        # create the dataframe
        df_m = pd.DataFrame(metrics)
        df_m.set_index('decade')
        return df_m
        
        
    def lda_info(self, decade):
        lda_model = self.models[decade]

        print("Perplexity: ", lda_model.get_perplexity())
        print("Coherence: ", lda_model.get_coherence())
        lda_model.plot_tsne()
        return lda_model.dashboard_LDAvis()

In [43]:
lda_models = LDAPipeline()

100%|██████████| 2611/2611 [00:00<00:00, 10696.58it/s]


In [44]:
lda_models.get_metrics()

decade  coherence  perplexity
0    1960   0.324538   -7.097046
1    1970   0.345557   -6.896585
2    1980   0.358477   -7.162287
3    1990   0.364500   -7.638484
4    2000   0.314609   -7.724586
5    2010   0.328314   -7.527402
6    2020   0.340090   -7.420807

Display information for each decade.

In [45]:
lda_1960 = lda_models.lda_info(1960)

Perplexity:  -7.097055971860833
Coherence:  0.324537797410485


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2579 samples in 0.002s...
[t-SNE] Computed neighbors for 2579 samples in 0.127s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2579
[t-SNE] Computed conditional probabilities for sample 2000 / 2579
[t-SNE] Computed conditional probabilities for sample 2579 / 2579
[t-SNE] Mean sigma: 0.003361


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] KL divergence after 250 iterations with early exaggeration: 64.482971
[t-SNE] KL divergence after 1000 iterations: 0.545339


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [46]:
lda_1960

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
5      0.110801 -0.007965       1        1  21.160775
7      0.101745 -0.080914       2        1  19.687676
8     -0.102101 -0.018312       3        1  10.836084
0     -0.105345  0.009925       4        1   9.612691
9     -0.053741  0.011562       5        1   8.098357
2      0.072707  0.004294       6        1   7.426176
6      0.019127 -0.019905       7        1   6.321367
3     -0.020238  0.093754       8        1   6.312827
1      0.042748  0.104886       9        1   5.470563
4     -0.065704 -0.097326      10        1   5.073485, topic_info=     Term         Freq        Total Category  logprob  loglift
8    love  6422.000000  6422.000000  Default  30.0000  30.0000
16   baby  3261.000000  3261.000000  Default  29.0000  29.0000
613    la   785.000000   785.000000  Default  28.0000  28.0000
32     oh  3223.000000  3223.000000  Default  27.0000  27.0000
58   know  3742.000000  3742.000000  Default  26.0000  26.0000
..    ...          ...          ...      ...      ...      ...
12    way    52.107578  1450.610777  Topic10  -5.4062  -0.3453
53     go    54.811313  2558.885040  Topic10  -5.3556  -0.8623
102  like    52.744441  2062.574632  Topic10  -5.3940  -0.6851
51    get    53.670076  2467.546290  Topic10  -5.3766  -0.8470
155   try    44.188555   792.334877  Topic10  -5.5710   0.0946

[788 rows x 6 columns], token_table=       Topic      Freq     Term
term                           
8850       3  0.870155       aa
12046      6  0.942578  abilene
2684       5  0.815777    actin
1056       1  0.052902   action
1056       2  0.026451   action
...      ...       ...      ...
471        7  0.015744     york
471        9  0.031489     york
471       10  0.078722     york
4897       7  0.080848     zone
4897      10  0.889328     zone

[2491 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[6, 8, 9, 1, 10, 3, 7, 4, 2, 5])

In [47]:
lda_1970 = lda_models.lda_info(1970)

Perplexity:  -6.896572983739439
Coherence:  0.34555685414543685


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2567 samples in 0.002s...
[t-SNE] Computed neighbors for 2567 samples in 0.114s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2567
[t-SNE] Computed conditional probabilities for sample 2000 / 2567
[t-SNE] Computed conditional probabilities for sample 2567 / 2567
[t-SNE] Mean sigma: 0.003386
[t-SNE] KL divergence after 250 iterations with early exaggeration: 64.845764
[t-SNE] KL divergence after 1000 iterations: 0.567434


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [48]:
lda_1970

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
4      0.067067  0.054981       1        1  24.942711
8      0.105631  0.006981       2        1  15.693118
1     -0.013586  0.060237       3        1  11.816222
7     -0.009700  0.071193       4        1  10.145058
5      0.012863  0.049998       5        1   8.739787
3     -0.065009 -0.051865       6        1   7.174041
6      0.057029 -0.028498       7        1   6.509052
9     -0.177038  0.034503       8        1   5.598840
0     -0.018209 -0.150305       9        1   4.729422
2      0.040952 -0.047225      10        1   4.651749, topic_info=      Term         Freq        Total Category  logprob  loglift
569     la  1268.000000  1268.000000  Default  30.0000  30.0000
281   baby  2953.000000  2953.000000  Default  29.0000  29.0000
160   love  7133.000000  7133.000000  Default  28.0000  28.0000
125     oh  3970.000000  3970.000000  Default  27.0000  27.0000
247   yeah  2778.000000  2778.000000  Default  26.0000  26.0000
..     ...          ...          ...      ...      ...      ...
304    hey    55.778680  1244.910796  Topic10  -5.3176  -0.0375
903  woman    49.787556   649.680851  Topic10  -5.4312   0.4992
331     go    58.464307  2990.316997  Topic10  -5.2705  -0.8668
335   time    51.027240  2416.176208  Topic10  -5.4066  -0.7897
236  night    49.076381  1239.589079  Topic10  -5.4456  -0.1612

[776 rows x 6 columns], token_table=      Topic      Freq        Term
term                             
9554     10  0.882244  additional
4314      4  0.962745        adio
8605      2  0.959803   aeroplane
6573      6  0.917893         aey
780       5  0.009626      africa
...     ...       ...         ...
3342      4  0.108222        zion
3342      8  0.021644        zion
3342      9  0.086578        zion
5390      1  0.021365         zip
5390      2  0.961421         zip

[2541 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[5, 9, 2, 8, 6, 4, 7, 10, 1, 3])

In [49]:
lda_1980 = lda_models.lda_info(1980)

Perplexity:  -7.162316937006045
Coherence:  0.3584769113613574


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2572 samples in 0.003s...
[t-SNE] Computed neighbors for 2572 samples in 0.120s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2572
[t-SNE] Computed conditional probabilities for sample 2000 / 2572
[t-SNE] Computed conditional probabilities for sample 2572 / 2572
[t-SNE] Mean sigma: 0.001623
[t-SNE] KL divergence after 250 iterations with early exaggeration: 61.638268
[t-SNE] KL divergence after 1000 iterations: 0.483344


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [50]:
lda_1980

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
1     -0.098721  0.015652       1        1  27.056529
0      0.014743  0.002609       2        1  14.749126
5     -0.019232  0.006858       3        1  12.729315
6     -0.032406  0.023755       4        1   8.758447
2     -0.026748  0.007999       5        1   7.645516
4     -0.015359  0.041542       6        1   7.489860
7     -0.050108  0.003210       7        1   6.440185
3     -0.033384  0.015235       8        1   6.181116
9      0.061913 -0.198126       9        1   4.512285
8      0.199303  0.081266      10        1   4.437621, topic_info=      Term         Freq        Total Category  logprob  loglift
20    love  6523.000000  6523.000000  Default  30.0000  30.0000
766     la   811.000000   811.000000  Default  29.0000  29.0000
115   want  2334.000000  2334.000000  Default  28.0000  28.0000
143    man  1514.000000  1514.000000  Default  27.0000  27.0000
87   night  1666.000000  1666.000000  Default  26.0000  26.0000
..     ...          ...          ...      ...      ...      ...
116    way    58.112642  1856.501806  Topic10  -5.3965  -0.3490
44    come    59.893356  2929.996776  Topic10  -5.3663  -0.7751
13      go    57.861246  3035.329157  Topic10  -5.4008  -0.8450
102    say    52.855115  1501.598580  Topic10  -5.4913  -0.2317
33    time    50.960614  2876.796010  Topic10  -5.5278  -0.9183

[790 rows x 6 columns], token_table=       Topic      Freq     Term
term                           
6293      10  0.896017       ac
11936     10  0.989600  acieeed
9151       3  0.969706       ag
9151       4  0.012929       ag
133        1  0.145348       ah
...      ...       ...      ...
755        5  0.010331     zone
755        6  0.041326     zone
755        8  0.196297     zone
755        9  0.010331     zone
1285      10  0.937112     zulu

[2534 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[2, 1, 6, 7, 3, 5, 8, 4, 10, 9])

In [51]:
lda_1990 = lda_models.lda_info(1990)

Perplexity:  -7.638478930678932
Coherence:  0.36450003540881293


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2584 samples in 0.002s...
[t-SNE] Computed neighbors for 2584 samples in 0.099s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2584
[t-SNE] Computed conditional probabilities for sample 2000 / 2584
[t-SNE] Computed conditional probabilities for sample 2584 / 2584
[t-SNE] Mean sigma: 0.003379
[t-SNE] KL divergence after 250 iterations with early exaggeration: 64.607819
[t-SNE] KL divergence after 1000 iterations: 0.547904


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [52]:
lda_1990

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
0     -0.025085 -0.031483       1        1  22.179345
7     -0.067208  0.042873       2        1  19.459545
1     -0.065975  0.052216       3        1  12.400144
8     -0.051249  0.068586       4        1  12.400128
9     -0.028523 -0.100442       5        1   7.332186
6     -0.010109 -0.103532       6        1   6.407230
4      0.021505  0.018304       7        1   6.375030
5     -0.003221 -0.058447       8        1   5.197690
2      0.020944  0.100147       9        1   4.331587
3      0.208921  0.011778      10        1   3.917115, topic_info=       Term         Freq        Total Category  logprob  loglift
166    love  4104.000000  4104.000000  Default  30.0000  30.0000
134    baby  1825.000000  1825.000000  Default  29.0000  29.0000
174      oh  2289.000000  2289.000000  Default  28.0000  28.0000
13     like  3285.000000  3285.000000  Default  27.0000  27.0000
436   chase   297.000000   297.000000  Default  26.0000  26.0000
...     ...          ...          ...      ...      ...      ...
1251   real    38.716185   564.525927  Topic10  -5.7261   0.5601
352    need    39.394184  1270.873543  Topic10  -5.7087  -0.2340
13     like    39.954653  3285.882302  Topic10  -5.6946  -1.1698
179   right    37.305639  1115.859772  Topic10  -5.7632  -0.1584
163    life    37.315677  1291.834234  Topic10  -5.7629  -0.3046

[794 rows x 6 columns], token_table=       Topic      Freq    Term
term                          
5618       1  0.976386   aaqil
12177      2  0.104341   aaron
12177      4  0.869512   aaron
12263      1  0.946212   adapt
1052       3  0.962201   admin
...      ...       ...     ...
403        9  0.006047      yo
403       10  0.001512      yo
1301       3  0.922163   zomba
1883       2  0.887620  zurich
15203      3  0.910420    über

[2773 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 8, 2, 9, 10, 7, 5, 6, 3, 4])

In [53]:
lda_2000 = lda_models.lda_info(2000)

Perplexity:  -7.724558635419135
Coherence:  0.3146094430813431


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2591 samples in 0.002s...
[t-SNE] Computed neighbors for 2591 samples in 0.122s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2591
[t-SNE] Computed conditional probabilities for sample 2000 / 2591
[t-SNE] Computed conditional probabilities for sample 2591 / 2591
[t-SNE] Mean sigma: 0.001936
[t-SNE] KL divergence after 250 iterations with early exaggeration: 63.588860
[t-SNE] KL divergence after 1000 iterations: 0.510394


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [54]:
lda_2000

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
6      0.011484  0.032902       1        1  26.607410
2      0.033855  0.036911       2        1  13.795715
5     -0.140517 -0.005887       3        1  11.723589
1      0.102453  0.053530       4        1  10.465244
7      0.020141  0.029607       5        1   9.746483
3      0.021575  0.024344       6        1   7.643510
4     -0.025685  0.008761       7        1   6.273375
8     -0.121679 -0.060059       8        1   5.540005
9     -0.000623  0.042696       9        1   4.144851
0      0.098996 -0.162804      10        1   4.059818, topic_info=     Term         Freq        Total Category  logprob  loglift
352    la   780.000000   780.000000  Default  30.0000  30.0000
39   love  2812.000000  2812.000000  Default  29.0000  29.0000
104  come  2578.000000  2578.000000  Default  28.0000  28.0000
92     be  1141.000000  1141.000000  Default  27.0000  27.0000
114   get  3027.000000  3027.000000  Default  26.0000  26.0000
..    ...          ...          ...      ...      ...      ...
196  know    51.808741  4053.029643  Topic10  -5.4976  -1.1556
39   love    48.470091  2812.960489  Topic10  -5.5642  -0.8570
130  lose    43.039007   709.734308  Topic10  -5.6831   0.4012
199   let    46.008411  1986.369470  Topic10  -5.6164  -0.5612
137    oh    45.112388  2415.705923  Topic10  -5.6360  -0.7766

[791 rows x 6 columns], token_table=       Topic      Freq   Term
term                         
9392       2  0.984994   aang
9392       5  0.004246   aang
9392      10  0.004246   aang
4350       2  0.054955  aaron
4350      10  0.879277  aaron
...      ...       ...    ...
16505      9  0.951322  zelda
3741       2  0.817570    zen
3741       6  0.158972    zen
5288       5  0.895187   zeta
12278      2  0.942345   zuko

[2661 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[7, 3, 6, 2, 8, 4, 5, 9, 10, 1])

In [55]:
lda_2010 = lda_models.lda_info(2010)

Perplexity:  -7.527411262433587
Coherence:  0.3283138788498487


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2590 samples in 0.003s...
[t-SNE] Computed neighbors for 2590 samples in 0.122s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2590
[t-SNE] Computed conditional probabilities for sample 2000 / 2590
[t-SNE] Computed conditional probabilities for sample 2590 / 2590
[t-SNE] Mean sigma: 0.002121
[t-SNE] KL divergence after 250 iterations with early exaggeration: 62.511276
[t-SNE] KL divergence after 1000 iterations: 0.485192


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [56]:
lda_2010

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
9      0.074265 -0.065518       1        1  24.870979
2     -0.101616 -0.039181       2        1  24.322598
0     -0.042311 -0.002322       3        1   9.542109
6     -0.068237 -0.028685       4        1   9.431371
4     -0.063437 -0.016150       5        1   8.152794
8      0.010254 -0.068791       6        1   7.989783
5     -0.004385  0.020207       7        1   5.124230
7      0.121568 -0.022403       8        1   4.186860
3     -0.060216  0.146991       9        1   3.566373
1      0.134116  0.075852      10        1   2.812904, topic_info=        Term         Freq        Total Category  logprob  loglift
13        oh  2601.000000  2601.000000  Default  30.0000  30.0000
335    bitch  1988.000000  1988.000000  Default  29.0000  29.0000
154     yeah  3552.000000  3552.000000  Default  28.0000  28.0000
842      aye   663.000000   663.000000  Default  27.0000  27.0000
193     come  2519.000000  2519.000000  Default  26.0000  26.0000
...      ...          ...          ...      ...      ...      ...
1348  fuckin    34.945874   296.224502  Topic10  -5.6558   1.4336
128     pull    35.826964   588.102609  Topic10  -5.6309   0.7728
107     fuck    39.304513  1990.128212  Topic10  -5.5382  -0.3537
335    bitch    36.707692  1988.772342  Topic10  -5.6066  -0.4213
88        be    33.996349  2109.448889  Topic10  -5.6833  -0.5570

[813 rows x 6 columns], token_table=       Topic      Freq      Term
term                            
15038      9  0.934008      aaah
13712      6  0.797572     abasi
1054       1  0.335929       act
1054       2  0.153670       act
1054       3  0.064327       act
...      ...       ...       ...
18467     10  0.829262     живём
18473     10  0.829304  настанет
18477     10  0.829234  ожидании
18484     10  0.829275       тот
18486     10  0.829109       час

[2654 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[10, 3, 1, 7, 5, 9, 6, 8, 4, 2])

In [57]:
lda_2020 = lda_models.lda_info(2020)

Perplexity:  -7.420831112191985
Coherence:  0.3400902450683902


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2579 samples in 0.002s...
[t-SNE] Computed neighbors for 2579 samples in 0.109s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2579
[t-SNE] Computed conditional probabilities for sample 2000 / 2579
[t-SNE] Computed conditional probabilities for sample 2579 / 2579
[t-SNE] Mean sigma: 0.003446
[t-SNE] KL divergence after 250 iterations with early exaggeration: 66.513138
[t-SNE] KL divergence after 1000 iterations: 0.591068


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [58]:
lda_2020

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
2     -0.097258  0.051897       1        1  19.987901
1      0.055168  0.031717       2        1  19.174756
5      0.105939 -0.000690       3        1  14.630263
9     -0.031495 -0.026716       4        1  10.641998
0      0.134937  0.099934       5        1   9.133672
6     -0.040696  0.041845       6        1   8.641477
7      0.090094 -0.122601       7        1   5.103785
8     -0.009147 -0.073323       8        1   4.505611
3     -0.137988 -0.014306       9        1   4.429232
4     -0.069553  0.012243      10        1   3.751306, topic_info=      Term         Freq        Total Category  logprob  loglift
250     oh  3678.000000  3678.000000  Default  30.0000  30.0000
271  bitch  2756.000000  2756.000000  Default  29.0000  29.0000
135   love  3737.000000  3737.000000  Default  28.0000  28.0000
34    yeah  6003.000000  6003.000000  Default  27.0000  27.0000
781     na   574.000000   574.000000  Default  26.0000  26.0000
..     ...          ...          ...      ...      ...      ...
264    ass    47.021113   472.840372  Topic10  -5.6791   0.9749
32   wanna    68.218353  2520.527001  Topic10  -5.3070  -0.3264
568   play    52.600048   816.583872  Topic10  -5.5670   0.5407
14    know    61.820488  5544.307426  Topic10  -5.4055  -1.2132
303   good    50.365459  1395.891804  Topic10  -5.6104  -0.0389

[826 rows x 6 columns], token_table=       Topic      Freq     Term
term                           
8507       4  0.945349  academy
7953       2  0.927401     acme
3343       2  0.120583   afford
3343       3  0.040194   afford
3343       4  0.060292   afford
...      ...       ...      ...
12202      1  0.906053       yé
12203      1  0.906058      zum
1813       1  0.935088     zuma
1813       3  0.044528     zuma
9360       9  0.939109  écoutez

[2779 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[3, 2, 6, 10, 1, 7, 8, 9, 4, 5])

Basic LDA model give us our baseline, we've got this default **perspicacity** and **coherence** score. Let's try to improve this to score and also our qualitative intuition about topic. As we saw topic seems really similar over the decade and it's quite difficult to retrieve some good topics given the representation we compute. 

## Improve the preprocessing

In this part, we will try to create a pre-processing function that can take into account bigrams and trigrams and also allow to put aside the terms that could have been too recurrent in the previous part.

### ngram recognition with gensim

A way to improve lyrics comprehension is to use bigram and trigram with the help of phraser in gensim.

In [59]:
import gensim

def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

# process in lyrics into words
data = sdf['lyrics'].tolist()
data_words = list(sent_to_words(data))

In [60]:
# display the result
data_words[0][:10]

['animal',
 'animal',
 'animal',
 'animal',
 'animal',
 'animal',
 'animal',
 'why',
 'don',
 'you']

In [61]:
import gensim

# Build the bigram and trigram models
bigram = gensim.models.Phrases(data_words, min_count=5, threshold=100) # higher threshold fewer phrases.
trigram = gensim.models.Phrases(bigram[data_words], threshold=100)  

# Faster way to get a sentence clubbed as a trigram/bigram
bigram_model = gensim.models.phrases.Phraser(bigram)
trigram_model = gensim.models.phrases.Phraser(trigram)

In [62]:
from numpy.random import randint, seed

# set seed from numpy
seed(18)

# draw the upper bound
upper_bound = randint(len(data_words))

# display a random example
print('bigram model: ', bigram_model[data_words[upper_bound]])
print('\ntrigram model: ', bigram_model[data_words[upper_bound]])
print('\nsentence: ',' '.join(data_words[upper_bound]))

bigram model:  ['beautiful', 'brother', 'of', 'mine', 'whatever', 'may', 'be', 'your', 'birth', 'sign', 'we', 'are', 'not', 'of', 'the', 'same', 'seed', 'although', 'we', 'are', 'both', 'the', 'same', 'breed', 'together', 'we', 're', 'truly', 'black', 'power', 'power', 'learning', 'to', 'trust', 'by', 'the', 'hour', 'hour', 'loving', 'our', 'women', 'now', 'more', 'we', 'love', 'more', 'respecting', 'what', 'black', 'is', 'now', 'for', 'and', 'we', 've', 'got', 'love', 'we', 've', 'got', 'love', 'we', 've', 'got', 'love', 'we', 'got', 'love', 'we', 've', 'got', 'love', 'we', 'got', 'love', 'beautiful', 'sister', 'of', 'mine', 'glad', 'we', 'both', 'think', 'it', 'now', 'time', 'to', 'really', 'show', 'what', 'we', 'can', 'do', 'improving', 'black', 'pride', 'is', 'now', 'true', 'at', 'last', 'we', 've', 'outgrown', 'uncle_tom', 'uncle_tom', 'devoting', 'more', 'time', 'in', 'the', 'slum', 'in', 'the', 'slum', 'showing', 'our', 'own', 'new', 'pride', 'we', 'have', 'pride', 'that', 'make

We are able to see some bigram and bigram, most of the time it's a words with its adjective or a group of onomatopeia.

As previously explained, we would also like to set aside irrelevant terms that may have been recurrent in our last analysis. If we look at the previous bar charts, we can observe a significant amount of these last terms over all the decades. This is the case for example of like, know or yeah. Most of the time these terms qualified as uninteresting are verbs or onomatopoeias. Let's try to identify the less interesting ones by comparing the bar charts with the visualizations of pyLDAvis. We can notice a strong recurrence of the verbs like, know, come, get which are not necessarily relevant because they are found in most of the analyzed topics. We can also find onomatopoeias oh, yeah and la in most of the topics.

In [63]:
# list recurrent terms
recurrent_terms = {'like','know','come','get', 'got','go','to','oh','yeah','la'}


# default preprocessing
def ngram_preprocess(text, nlp = new_nlp,
                     bigram = bigram_model,
                     trigram = trigram_model,
                    new_stopwords = recurrent_terms):
    
    # perform basic preprocessing to transform sentence to list of words
    words = gensim.utils.simple_preprocess(text)
    
    # customize stopwords
    spacy_stopwords = new_nlp.Defaults.stop_words
    ext_stopwords = spacy_stopwords | new_stopwords # union of set
    
    #removing stop words
    no_stop_words = [word for word in words if word not in ext_stopwords]
    
    # perform bigram model
    bigram_words = bigram[no_stop_words]
    
    # perform trigram model
    trigram_words = trigram[bigram_words]
    
    # recreate the sentence
    sentence = ' '.join(trigram_words)
    
    #tokenization to get lemma
    tokens = [token for token in nlp(sentence)]
    
    #LEMMATISATION and filter alphanumeric characters
    sentence = [word.lemma_ for word in tokens if word.text.isalpha()]

    return sentence

In [64]:
# test with the previously draw sentence
ngram_preprocess(' '.join(data_words[upper_bound]))[:10]

['beautiful',
 'brother',
 'birth',
 'sign',
 'seed',
 'breed',
 'truly',
 'black',
 'power',
 'power']

Let's try to rerun LDA with the new preprocessing function 

In [65]:
ngram_model = LDATopicModeling(decade = 2000, lang_preprocess = ngram_preprocess)

100%|██████████| 2611/2611 [00:00<00:00, 9191.93it/s]


In [66]:
ngram_model.dashboard_LDAvis()

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
7      0.178784  0.057699       1        1  17.461204
5     -0.051046 -0.078770       2        1  15.365419
0     -0.126361  0.073256       3        1  13.271933
8      0.022290 -0.015750       4        1  12.306393
2     -0.008340 -0.099695       5        1  10.361394
1      0.023596 -0.097160       6        1   8.300316
4      0.109230  0.007158       7        1   5.965658
3     -0.084899  0.010156       8        1   5.801452
6     -0.018587  0.122891       9        1   5.594882
9     -0.044668  0.020215      10        1   5.571351, topic_info=       Term         Freq        Total Category  logprob  loglift
39     love  2745.000000  2745.000000  Default  30.0000  30.0000
108     don  3822.000000  3822.000000  Default  29.0000  29.0000
162   wanna   993.000000   993.000000  Default  28.0000  28.0000
120      go  2369.000000  2369.000000  Default  27.0000  27.0000
1172  nigga   615.000000   615.000000  Default  26.0000  26.0000
...     ...          ...          ...      ...      ...      ...
664     god    59.414057   696.627782  Topic10  -5.6118   0.4258
222    well    59.848289   792.332331  Topic10  -5.6046   0.3044
132      ll    68.176898  2624.492994  Topic10  -5.4743  -0.7630
155    tell    63.063015  1313.533036  Topic10  -5.5522  -0.1488
39     love    67.771981  2745.561251  Topic10  -5.4802  -0.8141

[816 rows x 6 columns], token_table=       Topic      Freq        Term
term                              
17540      4  0.848505          aa
9577       2  0.996745        aang
17617      2  0.870581      abhore
7056       9  0.756394     abigail
12766      3  0.094171  accustomed
...      ...       ...         ...
16939      7  0.960012       zelda
3769       6  0.988184         zen
5360       6  0.958964        zeta
5361       6  0.924982       zetas
12573      3  0.966967        zuko

[2658 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[8, 6, 1, 9, 3, 2, 5, 4, 7, 10])

In [67]:
ngram_model.plot_tsne()

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2539 samples in 0.002s...
[t-SNE] Computed neighbors for 2539 samples in 0.107s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2539
[t-SNE] Computed conditional probabilities for sample 2000 / 2539
[t-SNE] Computed conditional probabilities for sample 2539 / 2539
[t-SNE] Mean sigma: 0.007436
[t-SNE] KL divergence after 250 iterations with early exaggeration: 69.108307
[t-SNE] KL divergence after 1000 iterations: 0.643453


Loading BokehJS ...

In [68]:
ngram_model = LDATopicModeling(decade = 2000,
                               lang_preprocess = ngram_preprocess,
                              cross_valid = True, epochs = 10)

total lda computation:  18
coherence: 0.33489674184535667
alpha: symmetric
eta: symmetric
topic: 2
coherence: 0.38592913363595605
alpha: asymmetric
eta: symmetric
topic: 2
coherence: 0.32876772075833516
alpha: symmetric
eta: symmetric
topic: 3
coherence: 0.3347526773811737
alpha: asymmetric
eta: symmetric
topic: 3
coherence: 0.34632884492259897
alpha: symmetric
eta: symmetric
topic: 4
coherence: 0.3284252748245064
alpha: asymmetric
eta: symmetric
topic: 4
coherence: 0.33929485865651554
alpha: symmetric
eta: symmetric
topic: 5
coherence: 0.3280032771407379
alpha: asymmetric
eta: symmetric
topic: 5
coherence: 0.30577232863665743
alpha: symmetric
eta: symmetric
topic: 6
coherence: 0.33044353448549296
alpha: asymmetric
eta: symmetric
topic: 6
coherence: 0.29943956439107894
alpha: symmetric
eta: symmetric
topic: 7
coherence: 0.3235262662598446
alpha: asymmetric
eta: symmetric
topic: 7
coherence: 0.3204302238221843
alpha: symmetric
eta: symmetric
topic: 8
coherence: 0.3067357330736096
alpha:

In [69]:
ngram_model.plot_coherence('alpha')

In [70]:
ngram_model.plot_tsne()

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2611 samples in 0.001s...
[t-SNE] Computed neighbors for 2611 samples in 0.031s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2611
[t-SNE] Computed conditional probabilities for sample 2000 / 2611
[t-SNE] Computed conditional probabilities for sample 2611 / 2611
[t-SNE] Mean sigma: 0.000087
[t-SNE] KL divergence after 250 iterations with early exaggeration: 50.646801
[t-SNE] KL divergence after 1000 iterations: 0.206112


Loading BokehJS ...

In [71]:
ngram_model.dashboard_LDAvis()

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



PreparedData(topic_coordinates=             x    y  topics  cluster       Freq
topic                                          
0      0.07003  0.0       1        1  62.476873
1     -0.07003  0.0       2        1  37.523127, topic_info=       Term         Freq        Total Category  logprob  loglift
89      ain  1305.000000  1305.000000  Default  30.0000  30.0000
750     man  1646.000000  1646.000000  Default  29.0000  29.0000
1172  nigga   567.000000   567.000000  Default  28.0000  28.0000
532    fuck   751.000000   751.000000  Default  27.0000  27.0000
211    shit   703.000000   703.000000  Default  26.0000  26.0000
...     ...          ...          ...      ...      ...      ...
262     say   364.190603  1008.600521   Topic2  -5.7060  -0.0384
158      to   403.379604  1534.416497   Topic2  -5.6038  -0.3558
77     time   432.599236  2235.131263   Topic2  -5.5339  -0.6620
156   think   389.756771  1404.844891   Topic2  -5.6382  -0.3019
133    look   359.055484  1207.202896   Topic2  -5.7202  -0.2324

[205 rows x 6 columns], token_table=       Topic      Freq   Term
term                         
9577       1  0.987417   aang
9577       2  0.012241   aang
89         1  0.222899    ain
89         2  0.776701    ain
10262      1  0.042250     ak
...      ...       ...    ...
3156       2  0.982891    yuh
16939      1  0.043942  zelda
16939      2  0.966722  zelda
3769       1  0.022892    zen
3769       2  0.984343    zen

[317 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2])

In [72]:
lda_cv_models = LDAPipeline(prep = ngram_preprocess, cv = True)

total lda computation:  18
coherence: 0.3483242262225434
alpha: symmetric
eta: symmetric
topic: 2
coherence: 0.3541359150892269
alpha: asymmetric
eta: symmetric
topic: 2
coherence: 0.3339099782037911
alpha: symmetric
eta: symmetric
topic: 3
coherence: 0.3532551364655984
alpha: asymmetric
eta: symmetric
topic: 3
coherence: 0.34537428557404815
alpha: symmetric
eta: symmetric
topic: 4
coherence: 0.3331298989017937
alpha: asymmetric
eta: symmetric
topic: 4
coherence: 0.3380812821135202
alpha: symmetric
eta: symmetric
topic: 5
coherence: 0.3510664492013623
alpha: asymmetric
eta: symmetric
topic: 5
coherence: 0.3202052533652072
alpha: symmetric
eta: symmetric
topic: 6
coherence: 0.3366565195218458
alpha: asymmetric
eta: symmetric
topic: 6
coherence: 0.33477173321951176
alpha: symmetric
eta: symmetric
topic: 7
coherence: 0.3277255889797041
alpha: asymmetric
eta: symmetric
topic: 7
coherence: 0.3224929210082502
alpha: symmetric
eta: symmetric
topic: 8
coherence: 0.33782573656787473
alpha: asym

In [73]:
lda_cv_models.get_metrics()

decade  coherence  perplexity
0    1960   0.354136   -7.171939
1    1970   0.435095   -7.026951
2    1980   0.409733   -7.244499
3    1990   0.407901   -7.729087
4    2000   0.358789   -7.781129
5    2010   0.402500   -7.616403
6    2020   0.391414   -7.543440

In [74]:
lda_cv_1960 = lda_cv_models.lda_info(1960)

Perplexity:  -7.171939203963953
Coherence:  0.3541359150892269


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2611 samples in 0.001s...
[t-SNE] Computed neighbors for 2611 samples in 0.031s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2611
[t-SNE] Computed conditional probabilities for sample 2000 / 2611
[t-SNE] Computed conditional probabilities for sample 2611 / 2611
[t-SNE] Mean sigma: 0.000081
[t-SNE] KL divergence after 250 iterations with early exaggeration: 50.681534
[t-SNE] KL divergence after 1000 iterations: 0.207166


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [75]:
lda_cv_1960

PreparedData(topic_coordinates=              x    y  topics  cluster       Freq
topic                                           
0      0.089539  0.0       1        1  64.871156
1     -0.089539  0.0       2        1  35.128844, topic_info=       Term         Freq        Total Category  logprob  loglift
9      love  5877.000000  5877.000000  Default  30.0000  30.0000
17     baby  3152.000000  3152.000000  Default  29.0000  29.0000
528   black   351.000000   351.000000  Default  28.0000  28.0000
62       to  1432.000000  1432.000000  Default  27.0000  27.0000
4529    jem   239.000000   239.000000  Default  26.0000  26.0000
...     ...          ...          ...      ...      ...      ...
14      way   229.065845  1422.925556   Topic2  -5.7877  -0.7803
594     hey   198.660481   677.517298   Topic2  -5.9301  -0.1807
199    tell   226.389211  1523.704560   Topic2  -5.7995  -0.8605
122    want   201.995475  1430.095878   Topic2  -5.9135  -0.9111
51     girl   199.613950  1269.540860   Topic2  -5.9254  -0.8039

[192 rows x 6 columns], token_table=       Topic      Freq     Term
term                           
12379      1  0.998312  abilene
1638       1  0.042899   africa
1638       2  0.986680   africa
1639       1  0.022819  african
1639       2  0.981200  african
...      ...       ...      ...
590        2  0.934810   yellow
206        1  0.849595      yes
206        2  0.150226      yes
733        1  0.367151    young
733        2  0.630879    young

[294 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2])

In [76]:
lda_cv_1970 = lda_cv_models.lda_info(1970)

Perplexity:  -7.026950613459042
Coherence:  0.4350950299107389


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2611 samples in 0.001s...
[t-SNE] Computed neighbors for 2611 samples in 0.027s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2611
[t-SNE] Computed conditional probabilities for sample 2000 / 2611
[t-SNE] Computed conditional probabilities for sample 2611 / 2611
[t-SNE] Mean sigma: 0.000415
[t-SNE] KL divergence after 250 iterations with early exaggeration: 50.350746
[t-SNE] KL divergence after 1000 iterations: 0.212509


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [77]:
lda_cv_1970

PreparedData(topic_coordinates=              x    y  topics  cluster       Freq
topic                                           
0      0.065293  0.0       1        1  55.673677
1     -0.065293  0.0       2        1  44.326323, topic_info=      Term         Freq        Total Category  logprob  loglift
156   love  6890.000000  6890.000000  Default  30.0000  30.0000
277   baby  2957.000000  2957.000000  Default  29.0000  29.0000
145    don  3510.000000  3510.000000  Default  28.0000  28.0000
233   need  1298.000000  1298.000000  Default  27.0000  27.0000
420  wanna   956.000000   956.000000  Default  26.0000  26.0000
..     ...          ...          ...      ...      ...      ...
156   love   620.812206  6890.023234   Topic2  -5.0624  -1.5932
159  right   386.862889  1177.107039   Topic2  -5.5353  -0.2992
434  thing   385.672466  1209.282027   Topic2  -5.5384  -0.3292
403   tell   396.896316  1490.914534   Topic2  -5.5097  -0.5099
298   good   355.940095  1492.035642   Topic2  -5.6186  -0.6195

[209 rows x 6 columns], token_table=      Topic      Freq    Term
term                         
775       1  0.027676  africa
775       2  0.968665  africa
721       1  0.780990     ain
721       2  0.219452     ain
8097      1  0.044983   annie
...     ...       ...     ...
675       2  0.892853    wind
1368      1  0.092541    wing
1368      2  0.913840    wing
720       1  0.911430      ya
720       2  0.087180      ya

[318 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2])

In [78]:
lda_cv_1980 = lda_cv_models.lda_info(1980)

Perplexity:  -7.244498526795922
Coherence:  0.4097330909303903


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2610 samples in 0.001s...
[t-SNE] Computed neighbors for 2610 samples in 0.032s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2610
[t-SNE] Computed conditional probabilities for sample 2000 / 2610
[t-SNE] Computed conditional probabilities for sample 2610 / 2610
[t-SNE] Mean sigma: 0.000640
[t-SNE] KL divergence after 250 iterations with early exaggeration: 52.454788
[t-SNE] KL divergence after 1000 iterations: 0.278725


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [79]:
lda_cv_1980

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
1     -0.063033  0.050386       1        1  41.476182
0     -0.035693 -0.060634       2        1  32.572455
2      0.098727  0.010248       3        1  25.951363, topic_info=       Term         Freq        Total Category  logprob  loglift
98     rock  1337.000000  1337.000000  Default  30.0000  30.0000
20     love  6033.000000  6033.000000  Default  29.0000  29.0000
37     baby  2582.000000  2582.000000  Default  28.0000  28.0000
283    beat   743.000000   743.000000  Default  27.0000  27.0000
90    party   486.000000   486.000000  Default  26.0000  26.0000
..      ...          ...          ...      ...      ...      ...
91   people   252.033159   776.982592   Topic3  -5.6089   0.2231
62     girl   292.296338  1595.730237   Topic3  -5.4607  -0.3484
113    want   308.584726  2256.487631   Topic3  -5.4065  -0.6406
111    turn   252.166079   959.348527   Topic3  -5.6084   0.0128
314    feel   280.302402  1938.609181   Topic3  -5.5026  -0.5849

[273 rows x 6 columns], token_table=      Topic      Freq   Term
term                        
281       3  0.982706    ace
9256      1  0.988265     ag
9256      3  0.012201     ag
131       1  0.145083     ah
131       2  0.361624     ah
...     ...       ...    ...
903       2  0.087038     yo
903       3  0.889031     yo
744       1  0.254673  young
744       2  0.162065  young
744       3  0.585417  young

[493 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[2, 1, 3])

In [80]:
lda_cv_1990 = lda_cv_models.lda_info(1990)

Perplexity:  -7.729082336625409
Coherence:  0.40790140460917135


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2605 samples in 0.002s...
[t-SNE] Computed neighbors for 2605 samples in 0.050s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2605
[t-SNE] Computed conditional probabilities for sample 2000 / 2605
[t-SNE] Computed conditional probabilities for sample 2605 / 2605
[t-SNE] Mean sigma: 0.000913
[t-SNE] KL divergence after 250 iterations with early exaggeration: 57.267273
[t-SNE] KL divergence after 1000 iterations: 0.372078


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [81]:
lda_cv_1990

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
2     -0.109663 -0.034054       1        1  30.821396
1     -0.046796 -0.012466       2        1  24.788042
0      0.009116  0.010143       3        1  19.048852
4      0.018184  0.082080       4        1  15.930336
3      0.129158 -0.045703       5        1   9.411374, topic_info=      Term         Freq        Total Category  logprob  loglift
145   love  4369.000000  4369.000000  Default  30.0000  30.0000
636   fuck   505.000000   505.000000  Default  29.0000  29.0000
248   shit   600.000000   600.000000  Default  28.0000  28.0000
229  nigga   502.000000   502.000000  Default  27.0000  27.0000
631  bitch   322.000000   322.000000  Default  26.0000  26.0000
..     ...          ...          ...      ...      ...      ...
141    let    91.047272  1826.686152   Topic5  -5.6654  -0.6356
300     go    93.123487  2349.134103   Topic5  -5.6428  -0.8646
19    tell    88.053216  1443.070857   Topic5  -5.6988  -0.4333
408  thing    82.042272  1185.247585   Topic5  -5.7695  -0.3072
112   baby    83.468449  1846.218125   Topic5  -5.7523  -0.7332

[443 rows x 6 columns], token_table=       Topic      Freq     Term
term                           
12372      3  0.037718    aaron
12372      4  0.113155    aaron
12372      5  0.829801    aaron
2213       1  0.081582  african
2213       2  0.843019  african
...      ...       ...      ...
378        3  0.446668       yo
378        4  0.214653       yo
378        5  0.195713       yo
15884      3  0.914162    zerop
15466      4  0.960492     über

[1003 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[3, 2, 1, 5, 4])

In [82]:
lda_cv_2000 = lda_cv_models.lda_info(2000)

Perplexity:  -7.781129537532919
Coherence:  0.35878949047147957


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2611 samples in 0.002s...
[t-SNE] Computed neighbors for 2611 samples in 0.030s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2611
[t-SNE] Computed conditional probabilities for sample 2000 / 2611
[t-SNE] Computed conditional probabilities for sample 2611 / 2611
[t-SNE] Mean sigma: 0.000105
[t-SNE] KL divergence after 250 iterations with early exaggeration: 50.578671
[t-SNE] KL divergence after 1000 iterations: 0.206774


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [83]:
lda_cv_2000

PreparedData(topic_coordinates=             x    y  topics  cluster       Freq
topic                                          
0      0.06639  0.0       1        1  58.638616
1     -0.06639  0.0       2        1  41.361384, topic_info=       Term         Freq        Total Category  logprob  loglift
89      ain  1300.000000  1300.000000  Default  30.0000  30.0000
1172  nigga   563.000000   563.000000  Default  29.0000  29.0000
532    fuck   745.000000   745.000000  Default  28.0000  28.0000
211    shit   698.000000   698.000000  Default  27.0000  27.0000
605     hey   768.000000   768.000000  Default  26.0000  26.0000
...     ...          ...          ...      ...      ...      ...
262     say   425.523602  1007.272864   Topic2  -5.6478   0.0211
77     time   499.503721  2242.949204   Topic2  -5.4875  -0.6191
163    want   462.791756  1685.974221   Topic2  -5.5638  -0.4100
1085     ve   411.358865  1668.290387   Topic2  -5.6816  -0.5173
232    girl   385.515309   877.667779   Topic2  -5.7465   0.0601

[210 rows x 6 columns], token_table=       Topic      Freq  Term
term                        
9577       1  0.994743  aang
9577       2  0.004044  aang
170        1  0.160230    ah
170        2  0.839020    ah
89         1  0.218371   ain
...      ...       ...   ...
12571      1  0.980342  ying
421        1  0.107908    yo
421        2  0.893376    yo
3156       1  0.029098   yuh
3156       2  0.989317   yuh

[327 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2])

In [84]:
lda_cv_2010 = lda_cv_models.lda_info(2010)

Perplexity:  -7.616403033438797
Coherence:  0.40250031771861566


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2610 samples in 0.001s...
[t-SNE] Computed neighbors for 2610 samples in 0.031s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2610
[t-SNE] Computed conditional probabilities for sample 2000 / 2610
[t-SNE] Computed conditional probabilities for sample 2610 / 2610
[t-SNE] Mean sigma: 0.000475
[t-SNE] KL divergence after 250 iterations with early exaggeration: 53.056549
[t-SNE] KL divergence after 1000 iterations: 0.276887


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [85]:
lda_cv_2010

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
2      0.106201  0.008043       1        1  39.324335
1     -0.039783 -0.052125       2        1  35.182547
0     -0.066418  0.044082       3        1  25.493119, topic_info=       Term         Freq        Total Category  logprob  loglift
333   bitch  1972.000000  1972.000000  Default  30.0000  30.0000
902   nigga  1254.000000  1254.000000  Default  29.0000  29.0000
903  niggas  1097.000000  1097.000000  Default  28.0000  28.0000
468    shit  1766.000000  1766.000000  Default  27.0000  27.0000
8      love  3230.000000  3230.000000  Default  26.0000  26.0000
..      ...          ...          ...      ...      ...      ...
125   leave   299.377698  1217.856340   Topic3  -5.6446  -0.0364
133     say   287.496116  1144.478039   Topic3  -5.6851  -0.0147
54     look   296.873981  1466.091498   Topic3  -5.6530  -0.2303
114      go   329.639341  2497.409873   Topic3  -5.5483  -0.6582
17    thing   267.832434   976.647712   Topic3  -5.7560   0.0730

[285 rows x 6 columns], token_table=       Topic      Freq   Term
term                         
1009       1  0.904849      I
1009       2  0.040718      I
1009       3  0.054291      I
1406       1  0.900740      a
1406       2  0.089386      a
...      ...       ...    ...
827        3  0.063621     yo
18236      2  0.922382  yooou
247        1  0.978651    yuh
247        2  0.014048    yuh
247        3  0.009365    yuh

[537 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[3, 2, 1])

In [86]:
lda_cv_2020 = lda_cv_models.lda_info(2020)

Perplexity:  -7.543440004951669
Coherence:  0.391414232140715


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2611 samples in 0.001s...
[t-SNE] Computed neighbors for 2611 samples in 0.029s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2611
[t-SNE] Computed conditional probabilities for sample 2000 / 2611
[t-SNE] Computed conditional probabilities for sample 2611 / 2611
[t-SNE] Mean sigma: 0.000089
[t-SNE] KL divergence after 250 iterations with early exaggeration: 50.392559
[t-SNE] KL divergence after 1000 iterations: 0.206876


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [87]:
lda_cv_2020

PreparedData(topic_coordinates=              x    y  topics  cluster       Freq
topic                                           
0      0.064566  0.0       1        1  58.500467
1     -0.064566  0.0       2        1  41.499533, topic_info=      Term         Freq        Total Category  logprob  loglift
273  bitch  2736.000000  2736.000000  Default  30.0000  30.0000
298   fuck  2293.000000  2293.000000  Default  29.0000  29.0000
139   love  3678.000000  3678.000000  Default  28.0000  28.0000
354     uh  1213.000000  1213.000000  Default  27.0000  27.0000
327  nigga  1223.000000  1223.000000  Default  26.0000  26.0000
..     ...          ...          ...      ...      ...      ...
522   talk   443.117473   934.450149   Topic2  -5.7562   0.1334
587   tell   512.143592  2070.855813   Topic2  -5.6114  -0.5176
248   look   473.005743  1501.258090   Topic2  -5.6909  -0.2755
29    time   492.643994  2423.989838   Topic2  -5.6502  -0.7139
707    say   450.551135  1381.566075   Topic2  -5.7395  -0.2410

[205 rows x 6 columns], token_table=      Topic      Freq   Term
term                        
0         1  0.236313      I
0         2  0.764204      I
265       1  0.219057     ah
265       2  0.781111     ah
266       1  0.391829    ain
...     ...       ...    ...
34        2  0.109244   wish
231       1  0.826446  world
231       2  0.173682  world
366       1  0.183138     yo
366       2  0.815983     yo

[319 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2])

## 2015 songs lyrics topic modelling

Let's first retrieve the english song in 2015 (year of with max genius lyrics repertoried).

Let's plot the tag distribution

The barplot below shows the frequency of each tag color by total views

Let's try topic modelling with top2vec library which is the easiest to start. But first let's filter the lyrics.

# 2000 song lyrics topic modelling

## References